# Google Colab initialization

In [38]:
# !pip install pyyaml==5.1

# import torch
# TORCH_VERSION = ".".join(torch.__version__.split(".")[:2])
# CUDA_VERSION = torch.__version__.split("+")[-1]
# print("torch: ", TORCH_VERSION, "; cuda: ", CUDA_VERSION)
# # Install detectron2 that matches the above pytorch version
# # See https://detectron2.readthedocs.io/tutorials/install.html for instructions
# !pip install detectron2 -f https://dl.fbaipublicfiles.com/detectron2/wheels/$CUDA_VERSION/torch$TORCH_VERSION/index.html > /dev/null 
# # If there is not yet a detectron2 release that matches the given torch + CUDA version, you need to install a different pytorch.

# exit(0)  # After installation, you may need to "restart runtime" in Colab. This line can also restart runtime

In [39]:
GOOGLE_COLAB = False
# GOOGLE_COLAB = True

In [40]:
if GOOGLE_COLAB == True:
    from google.colab import drive
    drive.mount('/content/drive/')

In [41]:
# if GOOGLE_COLAB == True:
#     !ls '/content/drive/MyDrive/18744/data/Cityscapes/'

#     !mkdir '/content/data/'
#     !mkdir '/content/data/Cityscapes/'

#     !unzip -n '/content/drive/MyDrive/18744/data/Cityscapes/gtFine_trainvaltest.zip' -d '/content/data/Cityscapes/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Cityscapes/leftImg8bit_trainvaltest.zip' -d '/content/data/Cityscapes/' > /dev/null
#     !tar -xf '/content/drive/MyDrive/18744/data/Cityscapes/mapped_labels.tar' --skip-old-files --directory '/content/data/Cityscapes/'

#     ##################################################

#     !ls '/content/drive/MyDrive/18744/data/Carla/packaging/'

#     !mkdir '/content/data/'
#     !mkdir '/content/data/Carla/'
#     !mkdir '/content/data/Carla/packaging/'

#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package2.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package3.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package4.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package5.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package6.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package7.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package8.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !unzip -n '/content/drive/MyDrive/18744/data/Carla/packaging/package9.zip' -d '/content/data/Carla/packaging/' > /dev/null
#     !tar -xf '/content/drive/MyDrive/18744/data/Carla/packaging/semantic_train.tar' --skip-old-files --directory '/content/data/Carla/packaging/'

#     ##################################################

#     !ls '/content/drive/MyDrive/18744/data/CarlaNight/night_packaging/'

#     !mkdir '/content/data/'
#     !mkdir '/content/data/CarlaNight/'
#     !mkdir '/content/data/CarlaNight/night_packaging/'
    
#     !tar -xf '/content/drive/MyDrive/18744/data/CarlaNight/night_packaging/package10.tar' --skip-old-files --directory '/content/data/CarlaNight/night_packaging/'
#     !tar -xf '/content/drive/MyDrive/18744/data/CarlaNight/night_packaging/package11.tar' --skip-old-files --directory '/content/data/CarlaNight/night_packaging/'

#     ##################################################

#     !ls '/content/drive/MyDrive/18744/data/RainAddition/train/'

#     !mkdir '/content/data/'
#     !mkdir '/content/data/RainAddition/'
#     !mkdir '/content/data/RainAddition/train/'

#     !tar -xf '/content/drive/MyDrive/18744/data/RainAddition/train/1.tar' --skip-old-files --directory '/content/data/RainAddition/train/'
#     !tar -xf '/content/drive/MyDrive/18744/data/RainAddition/train/2.tar' --skip-old-files --directory '/content/data/RainAddition/train/'
#     !tar -xf '/content/drive/MyDrive/18744/data/RainAddition/train/3.tar' --skip-old-files --directory '/content/data/RainAddition/train/'

In [42]:
if GOOGLE_COLAB == True:
    !ls '/content/drive/MyDrive/18744/data/'
    %cd '/content/drive/MyDrive/18744/Robust-Vision-in-Rain/Detectron2Predictor/'
    !ls

# Configs

In [43]:
main_dir = './'
#data_dir = '/home/tunx404/Miscellaneous/data/' # Local Jupyter
data_dir = '/home/gregory/Documents/RainPerception/'

if GOOGLE_COLAB == True:
    # data_dir = '/content/drive/MyDrive/18744/data/'
    data_dir = '/content/data/'
    
DEBUG = False
DEBUG = True

EVAL_LEVEL_LIST = ['H', 'M', 'S']
# EVAL_LEVEL_LIST = ['H']

# Libraries

In [44]:
##################################################
# Local libraries

from detectron2_predictor import Detectron2Predictor
from detectron2_trainer import Detectron2Trainer
from detectron2_dataset import Detectron2CustomDataset
from utilities import create_file_list, imshow_jupyter
from datasets import get_carla_file_list, get_carla_dicts, get_cityscapes_file_list, get_cityscapes_dicts
from datasets import convert_carla, convert_cityscapes

##################################################
# Libraries

import numpy as np
import torch
from torch import nn

import matplotlib.pyplot as plt
from PIL import Image

import os, json, cv2, random

##################################################
# Detectron2

import detectron2

from detectron2.utils.logger import setup_logger
setup_logger()

from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.utils.visualizer import Visualizer
from detectron2.data import DatasetCatalog

In [45]:
import sys
print(sys.version)

3.7.6 (default, May 29 2020, 16:22:44) 
[GCC 5.4.0 20160609]


# Image lists & dicts

## Carla

In [46]:
data_carla_dir = data_dir + 'Carla/packaging/'

# Dir structure:
# <data_carla_dir>
#     packages2
#     packages3
#     ...

data_carla_train_file_list = get_carla_file_list(data_carla_dir, packages=['package2', 'package3', 'package4', 'package5', 'package6', 'package7', 'package9', 'carla_data_day_2'], levels=['H', 'M', 'S'])
#data_carla_train_file_list = get_carla_file_list(data_carla_dir, packages=['package2'], levels=['H', 'M', 'S'])
# data_carla_val_file_list = get_carla_file_list(data_carla_dir, packages=['package8'], levels=['H', 'M', 'S'])
data_carla_val_file_list = get_carla_file_list(data_carla_dir, packages=['package8', 'carla_data_day_1'], levels=EVAL_LEVEL_LIST)

# # Toy example
# data_carla_train_file_list = data_carla_train_file_list[:10]
# data_carla_val_file_list = data_carla_val_file_list[:10]

Number of images: 8868
Number of images: 3258


In [47]:
# data_carla_dir = data_dir + 'RainRemoval/CarlaDerained/'

# # Dir structure:
# # <data_carla_dir>
# #     packages2
# #     packages3
# #     ...

# data_carla_train_file_list = get_carla_file_list(data_carla_dir, packages=['package8'], levels=EVAL_LEVEL_LIST)
# data_carla_val_file_list = get_carla_file_list(data_carla_dir, packages=['package8'], levels=EVAL_LEVEL_LIST)

# # # Toy example
# # data_carla_train_file_list = data_carla_train_file_list[:10]
# # data_carla_val_file_list = data_carla_val_file_list[:10]

In [48]:
print('**************************************************')
print('Carla clear')

def get_carla_clear_train_dicts():
    return get_carla_dicts(data_carla_train_file_list, data_carla_dir, clear=True, rain=False)

def get_carla_clear_val_dicts():
    return get_carla_dicts(data_carla_val_file_list, data_carla_dir, clear=True, rain=False)

if DEBUG == True:
    for dict in get_carla_clear_train_dicts()[:4]:
        print(dict)
    
print(len(get_carla_clear_train_dicts())) # 2990
print(len(get_carla_clear_val_dicts()))   # 1173

print('\n**************************************************')
print('Carla rain')

def get_carla_rain_train_dicts():
    return get_carla_dicts(data_carla_train_file_list, data_carla_dir, clear=False, rain=True)

def get_carla_rain_val_dicts():
    return get_carla_dicts(data_carla_val_file_list, data_carla_dir, clear=False, rain=True)

if DEBUG == True:
    for dict in get_carla_rain_val_dicts()[:4]:
        print(dict)
    
print(len(get_carla_rain_train_dicts())) # 2990
print(len(get_carla_rain_val_dicts()))   # 1173

print('\n**************************************************')
print('Carla all')

def get_carla_all_train_dicts():
    return get_carla_dicts(data_carla_train_file_list, data_carla_dir, clear=True, rain=True)

def get_carla_all_val_dicts():
    return get_carla_dicts(data_carla_val_file_list, data_carla_dir, clear=True, rain=True)

if DEBUG == True:
    for dict in get_carla_all_val_dicts()[:4]:
        print(dict)
    
print(len(get_carla_all_train_dicts())) # 2990*2 = 5980
print(len(get_carla_all_val_dicts()))   # 1173*2 = 2346

**************************************************
Carla clear
{'file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144040.0070002_clear.png', 'height': 720, 'width': 1280, 'image_id': '1647144040.0070002_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144040.0070002_semantic_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144051.8223236_clear.png', 'height': 720, 'width': 1280, 'image_id': '1647144051.8223236_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144051.8223236_semantic_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144063.4320533_clear.png', 'height': 720, 'width': 1280, 'image_id': '1647144063.4320533_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144063.4320533_semantic_train.png'}
{'file_name': '/hom

## Carla night

In [49]:
data_carla_night_dir = data_dir + 'CarlaNight/night_packaging/'

# Dir structure:
# <data_carla_night_dir>
#     packages10
#     packages11
#     ...

data_carla_night_train_file_list = get_carla_file_list(data_carla_night_dir, packages=['package10', 'carla_data_night_1', 'carla_data_night_3', 'carla_data_night_4'], levels=['H', 'M', 'S'])
# data_carla_night_val_file_list = get_carla_file_list(data_carla_night_dir, packages=['package11'], levels=['H', 'M', 'S'])
data_carla_night_val_file_list = get_carla_file_list(data_carla_night_dir, packages=['package11', 'carla_data_night_2'], levels=EVAL_LEVEL_LIST)

# # Toy example
# data_carla_night_train_file_list = data_carla_night_train_file_list[:10]
# data_carla_night_val_file_list = data_carla_night_val_file_list[:10]

Number of images: 7723
Number of images: 3273


In [50]:
print('**************************************************')
print('Carla night clear')

def get_carla_night_clear_train_dicts():
    return get_carla_dicts(data_carla_night_train_file_list, data_carla_night_dir, clear=True, rain=False)

def get_carla_night_clear_val_dicts():
    return get_carla_dicts(data_carla_night_val_file_list, data_carla_night_dir, clear=True, rain=False)

def get_carla_night_clear_val_dicts_sub():
    return get_carla_night_clear_val_dicts()[:1000]

if DEBUG == True:
    for dict in get_carla_night_clear_val_dicts()[:4]:
        print(dict)
    
print(len(get_carla_night_clear_train_dicts())) # 2842
print(len(get_carla_night_clear_val_dicts()))   # 2974

print('\n**************************************************')
print('Carla night rain')

def get_carla_night_rain_train_dicts():
    return get_carla_dicts(data_carla_night_train_file_list, data_carla_night_dir, clear=False, rain=True)

def get_carla_night_rain_val_dicts():
    return get_carla_dicts(data_carla_night_val_file_list, data_carla_night_dir, clear=False, rain=True)

if DEBUG == True:
    for dict in get_carla_night_rain_val_dicts()[:4]:
        print(dict)
    
print(len(get_carla_night_rain_train_dicts())) # 2842
print(len(get_carla_night_rain_val_dicts()))   # 2974

print('\n**************************************************')
print('Carla night all')

def get_carla_night_all_train_dicts():
    return get_carla_dicts(data_carla_night_train_file_list, data_carla_night_dir, clear=True, rain=True)

def get_carla_night_all_val_dicts():
    return get_carla_dicts(data_carla_night_val_file_list, data_carla_night_dir, clear=True, rain=True)

def get_carla_night_all_val_dicts_sub():
    return get_carla_night_clear_val_dicts()[:1000] + get_carla_night_rain_val_dicts()[:1000]

if DEBUG == True:
    for dict in get_carla_night_all_val_dicts()[:4]:
        print(dict)
    
print(len(get_carla_night_all_train_dicts())) # 2842*2 = 5684
print(len(get_carla_night_all_val_dicts()))   # 2974*2 = 5948

**************************************************
Carla night clear
{'file_name': '/home/gregory/Documents/RainPerception/CarlaNight/night_packaging/package11/1650004471.747364_clear.png', 'height': 720, 'width': 1280, 'image_id': '1650004471.747364_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/CarlaNight/night_packaging/package11/1650004471.747364_semantic_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/CarlaNight/night_packaging/package11/1650004480.8757513_clear.png', 'height': 720, 'width': 1280, 'image_id': '1650004480.8757513_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/CarlaNight/night_packaging/package11/1650004480.8757513_semantic_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/CarlaNight/night_packaging/package11/1650004489.9787946_clear.png', 'height': 720, 'width': 1280, 'image_id': '1650004489.9787946_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/CarlaNight/night_pack

## Cityscapes

In [51]:
data_dir_cityscapes = data_dir + 'Cityscapes/leftImg8bit/train/'
# data_dir_rain_addition = data_dir + 'RainAddition/train/'
data_dir_rain_addition = data_dir + 'RainRemoval/RainAddition/'
anno_dir_cityscapes = data_dir + 'Cityscapes/gtFine/train/'
# anno_dir_cityscapes = data_dir + 'Cityscapes/mapped_labels/train/'

city_name_list, _ = create_file_list(data_dir_cityscapes)
print(f'Number of cities: {len(city_name_list)}')

data_cityscapes_train_file_list = get_cityscapes_file_list(data_dir_cityscapes, cities=city_name_list[:13])
data_cityscapes_val_file_list   = get_cityscapes_file_list(data_dir_cityscapes, cities=city_name_list[13:])

# # Toy example
# data_cityscapes_train_file_list = data_cityscapes_train_file_list[:10]
# data_cityscapes_val_file_list = data_cityscapes_val_file_list[:10]

Number of cities: 18
Number of images: 2276
Number of images: 699


In [52]:
# data_dir_cityscapes = data_dir + 'RainRemoval/RainAddition/'
# # data_dir_rain_addition = data_dir + 'RainAddition/train/'
# data_dir_rain_addition = data_dir + 'RainRemoval/RainAddition/'
# # anno_dir_cityscapes = data_dir + 'Cityscapes/gtFine/train/'
# anno_dir_cityscapes = data_dir + 'Cityscapes/mapped_labels/train/'

# city_name_list, _ = create_file_list(data_dir_cityscapes)
# print(f'Number of cities: {len(city_name_list)}')

# data_cityscapes_train_file_list = get_cityscapes_file_list(data_dir_cityscapes, cities=city_name_list)
# data_cityscapes_val_file_list   = get_cityscapes_file_list(data_dir_cityscapes, cities=city_name_list)

# # # Toy example
# # data_cityscapes_train_file_list = data_cityscapes_train_file_list[:10]
# # data_cityscapes_val_file_list = data_cityscapes_val_file_list[:10

# def get_cityscapes_dicts(file_list, data_dir_main, data_dir_rain, anno_dir, clear=True, rain=True, levels=[]):
#     dicts = []
    
#     # for file in file_list:
#     for index, file in enumerate(file_list):
#         file_name, city = file

#         image_clear_path = os.path.join(data_dir_main, city, file_name)
        
#         file_name_split = file_name.split('_')
        
#         level = file_name_split[3][0]
        
#         # anno_name = file_name_split[0] + '_' + file_name_split[1] + '_' + file_name_split[2] + '_gtFine_labelIds.png' # Default
#         image_id = file_name_split[0] + '_' + file_name_split[1] + '_' + file_name_split[2]
#         anno_name = image_id + '_train.png' # Mapped
#         image_semantic_path = os.path.join(anno_dir, city, anno_name)
        
#         if level in levels:
#             if clear == True:
#                 record = {}
#                 record['file_name'] = image_clear_path
#                 record['height'] = 1024 # shape[0]
#                 record['width'] = 2048 # shape[1]
#                 record['image_id'] = image_id + '_clear'
#                 record['sem_seg_file_name'] = image_semantic_path
#                 dicts.append(record)

#             if rain == True:
#                 image_rain_name = image_id + '_' + level + '.png'
#                 image_rain_path = os.path.join(data_dir_rain, city, image_rain_name)

#                 record = {}
#                 record['file_name'] = image_rain_path
#                 record['height'] = 1024
#                 record['width'] = 2048
#                 record['image_id'] = image_id + '_rain'
#                 record['sem_seg_file_name'] = image_semantic_path
#                 dicts.append(record)
#     return dicts

In [53]:
print('**************************************************')
print('Cityscapes clear')

def get_cityscapes_clear_train_dicts():
    return get_cityscapes_dicts(data_cityscapes_train_file_list, data_dir_cityscapes, data_dir_rain_addition, anno_dir_cityscapes, clear=True, rain=False, levels=['H', 'M', 'S'])

def get_cityscapes_clear_val_dicts():
    return get_cityscapes_dicts(data_cityscapes_val_file_list, data_dir_cityscapes, data_dir_rain_addition, anno_dir_cityscapes, clear=True, rain=False, levels=['H', 'M', 'S'])

if DEBUG == True:
    for dict in get_cityscapes_clear_val_dicts()[:4]:
        print(dict)
    
print(len(get_cityscapes_clear_train_dicts())) # 2276
print(len(get_cityscapes_clear_val_dicts()))   # 699

print('\n**************************************************')
print('Cityscapes rain')

def get_cityscapes_rain_train_dicts():
    return get_cityscapes_dicts(data_cityscapes_train_file_list, data_dir_cityscapes, data_dir_rain_addition, anno_dir_cityscapes, clear=False, rain=True, levels=['H', 'M', 'S'])

def get_cityscapes_rain_val_dicts():
    # return get_cityscapes_dicts(data_cityscapes_val_file_list, data_dir_cityscapes, data_dir_rain_addition, anno_dir_cityscapes, clear=False, rain=True, levels=['H', 'M', 'S'])
    return get_cityscapes_dicts(data_cityscapes_val_file_list, data_dir_cityscapes, data_dir_rain_addition, anno_dir_cityscapes, clear=False, rain=True, levels=EVAL_LEVEL_LIST)

if DEBUG == True:
    for dict in get_cityscapes_rain_val_dicts()[:4]:
        print(dict)
    
print(len(get_cityscapes_rain_train_dicts())) # 2276
print(len(get_cityscapes_rain_val_dicts()))   # 699

print('\n**************************************************')
print('Cityscapes all')

def get_cityscapes_all_train_dicts():
    return get_cityscapes_dicts(data_cityscapes_train_file_list, data_dir_cityscapes, data_dir_rain_addition, anno_dir_cityscapes, clear=True, rain=True, levels=['H', 'M', 'S'])

def get_cityscapes_all_val_dicts():
    return get_cityscapes_dicts(data_cityscapes_val_file_list, data_dir_cityscapes, data_dir_rain_addition, anno_dir_cityscapes, clear=True, rain=True, levels=['H', 'M', 'S'])

if DEBUG == True:
    for dict in get_cityscapes_all_val_dicts()[:4]:
        print(dict)

print(len(get_cityscapes_all_train_dicts())) # 2276*2 = 4552
print(len(get_cityscapes_all_val_dicts()))   # 699*2  = 1398

**************************************************
Cityscapes clear
{'file_name': '/home/gregory/Documents/RainPerception/Cityscapes/leftImg8bit/train/stuttgart/stuttgart_000000_000019_leftImg8bit.png', 'height': 1024, 'width': 2048, 'image_id': 'stuttgart_000000_000019_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Cityscapes/gtFine/train/stuttgart/stuttgart_000000_000019_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/Cityscapes/leftImg8bit/train/stuttgart/stuttgart_000001_000019_leftImg8bit.png', 'height': 1024, 'width': 2048, 'image_id': 'stuttgart_000001_000019_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Cityscapes/gtFine/train/stuttgart/stuttgart_000001_000019_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/Cityscapes/leftImg8bit/train/stuttgart/stuttgart_000002_000019_leftImg8bit.png', 'height': 1024, 'width': 2048, 'image_id': 'stuttgart_000002_000019_clear', 'sem_seg_file_name': '/home/gregory/D

## Combined

In [54]:
print('**************************************************')
print('Combined clear')

def get_combined_clear_train_dicts():
    return get_carla_clear_train_dicts() + get_cityscapes_clear_train_dicts()

def get_combined_clear_val_dicts():
    return get_carla_clear_val_dicts() + get_cityscapes_clear_val_dicts()

if DEBUG == True:
    for dict in get_combined_clear_train_dicts()[:4]:
        print(dict)
    for dict in get_combined_clear_train_dicts()[-4:]:
        print(dict)
    
print(len(get_combined_clear_train_dicts())) # 2990 + 2276 = 5266
print(len(get_combined_clear_val_dicts()))   # 1173 + 699  = 1872

print('\n**************************************************')
print('Combined rain')

def get_combined_rain_train_dicts():
    return get_carla_rain_train_dicts() + get_cityscapes_rain_train_dicts()

def get_combined_rain_val_dicts():
    return get_carla_rain_val_dicts() + get_cityscapes_rain_val_dicts()

if DEBUG == True:
    for dict in get_combined_rain_train_dicts()[:4]:
        print(dict)
    for dict in get_combined_rain_train_dicts()[-4:]:
        print(dict)
    
print(len(get_combined_rain_train_dicts())) # 2990 + 2276 = 5266
print(len(get_combined_rain_val_dicts()))   # 1173 + 699  = 1872

print('\n**************************************************')
print('Combined all')

def get_combined_all_train_dicts():
    return get_carla_all_train_dicts() + get_cityscapes_all_train_dicts()

def get_combined_all_val_dicts():
    return get_carla_all_val_dicts()[:1000] + get_cityscapes_all_val_dicts()[:1000]

if DEBUG == True:
    for dict in get_combined_all_train_dicts()[:4]:
        print(dict)
    for dict in get_combined_all_train_dicts()[-4:]:
        print(dict)

print(len(get_combined_all_train_dicts())) # 5266*2 = 10532
print(len(get_combined_all_val_dicts()))   # 1872*2 = 3744

print('\n**************************************************')
print('Combined all night')

def get_combined_clear_both_train_dicts():
    return get_combined_clear_train_dicts() + get_carla_night_clear_train_dicts()

def get_combined_clear_both_val_dicts():
    return get_combined_clear_val_dicts() + get_carla_night_clear_val_dicts()[:1000]

def get_combined_all_night_train_dicts():
    return get_combined_all_train_dicts() + get_carla_night_all_train_dicts()

def get_combined_all_night_val_dicts():
    return get_combined_all_val_dicts() + get_carla_night_all_val_dicts()[:1000]

if DEBUG == True:
    for dict in get_combined_all_night_train_dicts()[:4]:
        print(dict)
    for dict in get_combined_all_night_val_dicts()[-4:]:
        print(dict)

print(len(get_combined_all_night_train_dicts())) # 10532 + 5684 = 16216
print(len(get_combined_all_night_val_dicts()))   # 3744  + 5948 = 9692

**************************************************
Combined clear
{'file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144040.0070002_clear.png', 'height': 720, 'width': 1280, 'image_id': '1647144040.0070002_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144040.0070002_semantic_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144051.8223236_clear.png', 'height': 720, 'width': 1280, 'image_id': '1647144051.8223236_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144051.8223236_semantic_train.png'}
{'file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144063.4320533_clear.png', 'height': 720, 'width': 1280, 'image_id': '1647144063.4320533_clear', 'sem_seg_file_name': '/home/gregory/Documents/RainPerception/Carla/packaging/package2/1647144063.4320533_semantic_train.png'}
{'file_name': '/

37734
3000


# Convert labels to train IDs
Execute only once

In [55]:
# %cd '/home/tunx404/Miscellaneous/data/Cityscapes/mapped_labels/train/'
# for city_name in city_name_list:
#     !mkdir $city_name

In [56]:
# convert_carla(data_carla_train_file_list, data_carla_dir)
# convert_carla(data_carla_val_file_list, data_carla_dir)

convert_carla(data_carla_night_train_file_list, data_carla_night_dir)
convert_carla(data_carla_night_val_file_list, data_carla_night_dir)

# convert_cityscapes(data_cityscapes_train_file_list, anno_dir_cityscapes, output_dir='/home/gregory/Documents/RainPerception/Cityscapes/gtFine/train/')
# convert_cityscapes(data_cityscapes_val_file_list, anno_dir_cityscapes, output_dir='/home/gregory/Documents/RainPerception/Cityscapes/gtFine/train/')

100%|█████████████████████| 3273/3273 [01:32<00:00, 35.42it/s]


# Datasets

In [57]:
DatasetCatalog.clear()

print('**************************************************')

print('Carla clear dataset')
carla_clear_dataset = Detectron2CustomDataset('carla_clear_train', 'carla_clear_val', get_carla_clear_train_dicts, get_carla_clear_val_dicts)
# carla_clear_dataset.visualize_dataset(num_samples=4, size=(20, 10), show_original=True)
            
print('\nCarla rain dataset')
carla_rain_dataset = Detectron2CustomDataset('carla_rain_train', 'carla_rain_val', get_carla_rain_train_dicts, get_carla_rain_val_dicts)
# carla_rain_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)

# print('\nCarla derained dataset')
# carla_derained_dataset = Detectron2CustomDataset('carla_derained_train', 'carla_derained_val', get_carla_rain_train_dicts, get_carla_derained_val_dicts)
# # carla_rain_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)

##################################################

print('\n**************************************************')

print('Carla night clear dataset')
carla_night_clear_dataset = Detectron2CustomDataset('carla_night_clear_train', 'carla_night_clear_val', get_carla_night_clear_train_dicts, get_carla_night_clear_val_dicts_sub)
# carla_night_clear_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)
            
print('\nCarla night rain dataset')
carla_night_rain_dataset = Detectron2CustomDataset('carla_night_rain_train', 'carla_night_rain_val', get_carla_night_rain_train_dicts, get_carla_night_rain_val_dicts)
# carla_night_rain_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)

print('\nCarla night all dataset')
carla_night_all_dataset = Detectron2CustomDataset('carla_night_all_train', 'carla_night_all_val', get_carla_night_all_train_dicts, get_carla_night_all_val_dicts_sub)
# carla_night_all_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)

##################################################

print('\n**************************************************')

print('Cityscapes clear dataset')
cityscapes_clear_dataset = Detectron2CustomDataset('cityscapes_clear_train', 'cityscapes_clear_val', get_cityscapes_clear_train_dicts, get_cityscapes_clear_val_dicts)
# cityscapes_clear_dataset.visualize_dataset(num_samples=10, size=(20, 10), show_original=True)

print('\nCityscapes rain dataset')
cityscapes_rain_dataset = Detectron2CustomDataset('cityscapes_rain_train', 'cityscapes_rain_val', get_cityscapes_rain_train_dicts, get_cityscapes_rain_val_dicts)
# cityscapes_rain_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)

##################################################

print('\n**************************************************')
            
print('Combined clear dataset')
combined_clear_dataset = Detectron2CustomDataset('combined_clear_train', 'combined_clear_val', get_combined_clear_train_dicts, get_combined_clear_val_dicts)
# combined_clear_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)
            
print('\nCombined rain dataset')
combined_rain_dataset = Detectron2CustomDataset('combined_rain_train', 'combined_rain_val', get_combined_rain_train_dicts, get_combined_rain_val_dicts)
# combined_rain_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)
            
print('\nCombined all dataset')
combined_all_dataset = Detectron2CustomDataset('combined_all_train', 'combined_all_val', get_combined_all_train_dicts, get_combined_all_val_dicts)
# combined_all_dataset.visualize_dataset(num_samples=1, size=(20, 10), show_original=True)

##################################################

print('\n**************************************************')
            
print('Combined all night dataset (rain+clear, day+night)')
combined_all_night_dataset = Detectron2CustomDataset('combined_all_night_train', 'combined_all_night_val', get_combined_all_night_train_dicts, get_combined_all_night_val_dicts)
# combined_all_dataset.visualize_dataset(num_samples=20, size=(20, 10), show_original=True)

print('\nCombined clear both dataset')
combined_all_night_dataset = Detectron2CustomDataset('combined_clear_both_train', 'combined_clear_both_val', get_combined_clear_both_train_dicts, get_combined_clear_both_val_dicts)
# combined_all_dataset.visualize_dataset(num_samples=20, size=(20, 10), show_original=True)

**************************************************
Carla clear dataset
Number of train images: 8868
Number of val images:   3258

Carla rain dataset
Number of train images: 8868
Number of val images:   3258

**************************************************
Carla night clear dataset
Number of train images: 7723
Number of val images:   1000

Carla night rain dataset
Number of train images: 7723
Number of val images:   3273

Carla night all dataset
Number of train images: 15446
Number of val images:   2000

**************************************************
Cityscapes clear dataset
Number of train images: 2276
Number of val images:   699

Cityscapes rain dataset
Number of train images: 2276
Number of val images:   699

**************************************************
Combined clear dataset
Number of train images: 11144
Number of val images:   3957

Combined rain dataset
Number of train images: 11144
Number of val images:   3957

Combined all dataset
Number of train images: 22288
Numbe

# Train

In [21]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '1, 2, 3'
os.environ["CUDA_LAUNCH_BLOCKING"] = "1"
print(os.environ['CUDA_VISIBLE_DEVICES'])
print(torch.cuda.is_available())

1, 2, 3
True


In [22]:
#trainer_all = Detectron2Trainer('combined_all_night_train', 'combined_all_night_val', output_folder='./output_part_night_40k')
#trainer_all.load()
#trainer_all.train()

In [23]:
#trainer_clear = Detectron2Trainer('cityscapes_clear_train', 'cityscapes_clear_val', output_folder='./output_combined_all_40k')
#trainer_clear.load()
#detectron2.engine.launch(trainer_clear.train, 3)
#trainer_clear.train()

In [24]:
#trainer_clear.train()

In [25]:
# %load_ext tensorboard
# %tensorboard --logdir output_all_40k

In [26]:
# %load_ext tensorboard
# %tensorboard --logdir output_clear_20k

## Models for Construction

### -3. Day Clear

In [27]:
trainer_all = Detectron2Trainer('combined_clear_train', 'combined_clear_val', output_folder='./output_day_clear_40k')
trainer_all.load()
trainer_all.train()

17
[06/28 20:49:19 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/28 20:49:19 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/28 20:49:19 d2.data.build]: Using training sampler TrainingSampler
[06/28 20:49:19 d2.data.common]: Serializing 11144 elements to byte tensors and concatenating them all ...
[06/28 20:49:19 d2.data.common]: Serialized dataset takes 3.42 MiB
[06/28 20:49:20 d2.checkpoint.c2_model_loading]: Renaming Caffe2 weights ......
[06/28 20:49:20 d2.checkpoint.c2_model_loading]: Following weights matched with submodule backbone.bottom_up:
| Names in Model    | Names in Checkpoint      | Shapes                                          |
|:------------------|:-------------------------|:------------------------------------------------|
| res2.0.conv1.*    | res2_0_branch2a_{bn_*,w} | (64,) (64,) (64,) (64,) (64,64,1,1)             |
| res2.0.conv2.*    | res2_0_branch2b_{bn_*,w} | (64,) (64,) (64,) (64,) (64

Some model parameters or buffers are not found in the checkpoint:
backbone.fpn_lateral2.{bias, weight}
backbone.fpn_lateral3.{bias, weight}
backbone.fpn_lateral4.{bias, weight}
backbone.fpn_lateral5.{bias, weight}
backbone.fpn_output2.{bias, weight}
backbone.fpn_output3.{bias, weight}
backbone.fpn_output4.{bias, weight}
backbone.fpn_output5.{bias, weight}
sem_seg_head.p2.0.norm.{bias, weight}
sem_seg_head.p2.0.weight
sem_seg_head.p3.0.norm.{bias, weight}
sem_seg_head.p3.0.weight
sem_seg_head.p4.0.norm.{bias, weight}
sem_seg_head.p4.0.weight
sem_seg_head.p4.2.norm.{bias, weight}
sem_seg_head.p4.2.weight
sem_seg_head.p5.0.norm.{bias, weight}
sem_seg_head.p5.0.weight
sem_seg_head.p5.2.norm.{bias, weight}
sem_seg_head.p5.2.weight
sem_seg_head.p5.4.norm.{bias, weight}
sem_seg_head.p5.4.weight
sem_seg_head.predictor.{bias, weight}
The checkpoint state_dict contains keys that are not used by the model:
  fc1000.{bias, weight}
  stem.conv1.bias


[06/28 20:49:20 d2.engine.train_loop]: Starting training from iteration 0
[06/28 20:49:29 d2.utils.events]:  eta: 4:41:04  iter: 19  total_loss: 4.502  time: 0.4220  data_time: 0.0268  lr: 0.00019981  max_mem: 4306M
[06/28 20:49:38 d2.utils.events]:  eta: 4:57:21  iter: 39  total_loss: 1.166  time: 0.4297  data_time: 0.0080  lr: 0.00039961  max_mem: 4306M
[06/28 20:49:46 d2.utils.events]:  eta: 4:59:40  iter: 59  total_loss: 0.6399  time: 0.4348  data_time: 0.0072  lr: 0.00059941  max_mem: 4306M
[06/28 20:49:55 d2.utils.events]:  eta: 4:59:43  iter: 79  total_loss: 0.5251  time: 0.4352  data_time: 0.0078  lr: 0.00079921  max_mem: 4306M
[06/28 20:50:04 d2.utils.events]:  eta: 5:00:06  iter: 99  total_loss: 0.5044  time: 0.4368  data_time: 0.0071  lr: 0.00099901  max_mem: 4306M
[06/28 20:50:13 d2.utils.events]:  eta: 4:59:57  iter: 119  total_loss: 0.3507  time: 0.4370  data_time: 0.0075  lr: 0.0011988  max_mem: 4306M
[06/28 20:50:22 d2.utils.events]:  eta: 5:00:29  iter: 139  total_loss

[06/28 20:57:42 d2.utils.events]:  eta: 5:06:38  iter: 1099  total_loss: 0.1891  time: 0.4554  data_time: 0.0080  lr: 0.01  max_mem: 4306M
[06/28 20:57:51 d2.utils.events]:  eta: 5:06:52  iter: 1119  total_loss: 0.1843  time: 0.4556  data_time: 0.0077  lr: 0.01  max_mem: 4306M
[06/28 20:58:01 d2.utils.events]:  eta: 5:07:09  iter: 1139  total_loss: 0.2139  time: 0.4558  data_time: 0.0082  lr: 0.01  max_mem: 4306M
[06/28 20:58:10 d2.utils.events]:  eta: 5:07:12  iter: 1159  total_loss: 0.1826  time: 0.4559  data_time: 0.0081  lr: 0.01  max_mem: 4306M
[06/28 20:58:19 d2.utils.events]:  eta: 5:07:12  iter: 1179  total_loss: 0.1995  time: 0.4560  data_time: 0.0079  lr: 0.01  max_mem: 4306M
[06/28 20:58:28 d2.utils.events]:  eta: 5:07:16  iter: 1199  total_loss: 0.2011  time: 0.4560  data_time: 0.0075  lr: 0.01  max_mem: 4306M
[06/28 20:58:37 d2.utils.events]:  eta: 5:07:26  iter: 1219  total_loss: 0.2204  time: 0.4561  data_time: 0.0074  lr: 0.01  max_mem: 4306M
[06/28 20:58:47 d2.utils.ev

...

[06/29 03:50:13 d2.evaluation.evaluator]: Inference done 3130/3957. Dataloading: 0.0021 s/iter. Inference: 0.0472 s/iter. Eval: 0.0363 s/iter. Total: 0.0858 s/iter. ETA=0:01:10
[06/29 03:50:18 d2.evaluation.evaluator]: Inference done 3190/3957. Dataloading: 0.0021 s/iter. Inference: 0.0472 s/iter. Eval: 0.0363 s/iter. Total: 0.0858 s/iter. ETA=0:01:05
[06/29 03:50:24 d2.evaluation.evaluator]: Inference done 3249/3957. Dataloading: 0.0021 s/iter. Inference: 0.0472 s/iter. Eval: 0.0363 s/iter. Total: 0.0858 s/iter. ETA=0:01:00
[06/29 03:50:29 d2.evaluation.evaluator]: Inference done 3280/3957. Dataloading: 0.0021 s/iter. Inference: 0.0473 s/iter. Eval: 0.0370 s/iter. Total: 0.0865 s/iter. ETA=0:00:58
[06/29 03:50:34 d2.evaluation.evaluator]: Inference done 3305/3957. Dataloading: 0.0021 s/iter. Inference: 0.0474 s/iter. Eval: 0.0378 s/iter. Total: 0.0874 s/iter. ETA=0:00:56
[06/29 03:50:39 d2.evaluation.evaluator]: Inference done 3330/3957. Dataloading: 0.0021 s/iter. Inference: 0.0475 s

[06/29 03:53:29 d2.utils.events]:  eta: 0:15:14  iter: 38099  total_loss: 0.06447  time: 0.4598  data_time: 0.0096  lr: 1e-06  max_mem: 4306M
[06/29 03:53:38 d2.utils.events]:  eta: 0:15:03  iter: 38119  total_loss: 0.07084  time: 0.4598  data_time: 0.0086  lr: 1e-06  max_mem: 4306M
[06/29 03:53:47 d2.utils.events]:  eta: 0:14:53  iter: 38139  total_loss: 0.07256  time: 0.4598  data_time: 0.0093  lr: 1e-06  max_mem: 4306M
[06/29 03:53:56 d2.utils.events]:  eta: 0:14:43  iter: 38159  total_loss: 0.06705  time: 0.4598  data_time: 0.0101  lr: 1e-06  max_mem: 4306M
[06/29 03:54:06 d2.utils.events]:  eta: 0:14:34  iter: 38179  total_loss: 0.07305  time: 0.4598  data_time: 0.0096  lr: 1e-06  max_mem: 4306M
[06/29 03:54:15 d2.utils.events]:  eta: 0:14:25  iter: 38199  total_loss: 0.07616  time: 0.4598  data_time: 0.0097  lr: 1e-06  max_mem: 4306M
[06/29 03:54:24 d2.utils.events]:  eta: 0:14:15  iter: 38219  total_loss: 0.06714  time: 0.4598  data_time: 0.0094  lr: 1e-06  max_mem: 4306M
[06/29

[06/29 04:02:05 d2.utils.events]:  eta: 0:06:28  iter: 39199  total_loss: 0.07014  time: 0.4600  data_time: 0.0091  lr: 1e-06  max_mem: 4306M
[06/29 04:02:14 d2.utils.events]:  eta: 0:06:19  iter: 39219  total_loss: 0.06903  time: 0.4600  data_time: 0.0092  lr: 1e-06  max_mem: 4306M
[06/29 04:02:24 d2.utils.events]:  eta: 0:06:09  iter: 39239  total_loss: 0.07327  time: 0.4600  data_time: 0.0088  lr: 1e-06  max_mem: 4306M
[06/29 04:02:33 d2.utils.events]:  eta: 0:05:59  iter: 39259  total_loss: 0.074  time: 0.4600  data_time: 0.0086  lr: 1e-06  max_mem: 4306M
[06/29 04:02:42 d2.utils.events]:  eta: 0:05:50  iter: 39279  total_loss: 0.07436  time: 0.4600  data_time: 0.0097  lr: 1e-06  max_mem: 4306M
[06/29 04:02:52 d2.utils.events]:  eta: 0:05:40  iter: 39299  total_loss: 0.07623  time: 0.4600  data_time: 0.0092  lr: 1e-06  max_mem: 4306M
[06/29 04:03:01 d2.utils.events]:  eta: 0:05:30  iter: 39319  total_loss: 0.07966  time: 0.4600  data_time: 0.0091  lr: 1e-06  max_mem: 4306M
[06/29 0

[06/29 04:09:03 d2.evaluation.evaluator]: Inference done 484/3957. Dataloading: 0.0019 s/iter. Inference: 0.0474 s/iter. Eval: 0.0359 s/iter. Total: 0.0853 s/iter. ETA=0:04:56
[06/29 04:09:08 d2.evaluation.evaluator]: Inference done 544/3957. Dataloading: 0.0019 s/iter. Inference: 0.0473 s/iter. Eval: 0.0359 s/iter. Total: 0.0852 s/iter. ETA=0:04:50
[06/29 04:09:13 d2.evaluation.evaluator]: Inference done 603/3957. Dataloading: 0.0019 s/iter. Inference: 0.0473 s/iter. Eval: 0.0358 s/iter. Total: 0.0852 s/iter. ETA=0:04:45
[06/29 04:09:18 d2.evaluation.evaluator]: Inference done 662/3957. Dataloading: 0.0020 s/iter. Inference: 0.0472 s/iter. Eval: 0.0359 s/iter. Total: 0.0852 s/iter. ETA=0:04:40
[06/29 04:09:23 d2.evaluation.evaluator]: Inference done 721/3957. Dataloading: 0.0020 s/iter. Inference: 0.0472 s/iter. Eval: 0.0360 s/iter. Total: 0.0852 s/iter. ETA=0:04:35
[06/29 04:09:28 d2.evaluation.evaluator]: Inference done 779/3957. Dataloading: 0.0020 s/iter. Inference: 0.0472 s/iter.

[06/29 04:12:50 d2.evaluation.evaluator]: Inference done 3129/3957. Dataloading: 0.0021 s/iter. Inference: 0.0470 s/iter. Eval: 0.0365 s/iter. Total: 0.0857 s/iter. ETA=0:01:10
[06/29 04:12:55 d2.evaluation.evaluator]: Inference done 3188/3957. Dataloading: 0.0021 s/iter. Inference: 0.0470 s/iter. Eval: 0.0365 s/iter. Total: 0.0857 s/iter. ETA=0:01:05
[06/29 04:13:00 d2.evaluation.evaluator]: Inference done 3247/3957. Dataloading: 0.0021 s/iter. Inference: 0.0470 s/iter. Eval: 0.0365 s/iter. Total: 0.0857 s/iter. ETA=0:01:00
[06/29 04:13:05 d2.evaluation.evaluator]: Inference done 3279/3957. Dataloading: 0.0021 s/iter. Inference: 0.0471 s/iter. Eval: 0.0372 s/iter. Total: 0.0864 s/iter. ETA=0:00:58
[06/29 04:13:10 d2.evaluation.evaluator]: Inference done 3305/3957. Dataloading: 0.0021 s/iter. Inference: 0.0472 s/iter. Eval: 0.0380 s/iter. Total: 0.0873 s/iter. ETA=0:00:56
[06/29 04:13:15 d2.evaluation.evaluator]: Inference done 3330/3957. Dataloading: 0.0021 s/iter. Inference: 0.0473 s

### -2. Night Clear

In [28]:
trainer_all = Detectron2Trainer('carla_night_clear_train', 'carla_night_clear_val', output_folder='./output_night_clear_40k')
trainer_all.load()
trainer_all.train()

17
[06/29 04:15:19 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/29 04:15:19 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/29 04:15:19 d2.data.build]: Using training sampler TrainingSampler
[06/29 04:15:19 d2.data.common]: Serializing 7723 elements to byte tensors and concatenating them all ...
[06/29 04:15:19 d2.data.common]: Serialized dataset takes 2.52 MiB
[06/29 04:15:19 d2.checkpoint.c2_model_loading]: Renaming Caffe2 weights ......
[06/29 04:15:19 d2.checkpoint.c2_model_loading]: Following weights matched with submodule backbone.bottom_up:
| Names in Model    | Names in Checkpoint      | Shapes                                          |
|:------------------|:-------------------------|:------------------------------------------------|
| res2.0.conv1.*    | res2_0_branch2a_{bn_*,w} | (64,) (64,) (64,) (64,) (64,64,1,1)             |
| res2.0.conv2.*    | res2_0_branch2b_{bn_*,w} | (64,) (64,) (64,) (64,) (64,

Some model parameters or buffers are not found in the checkpoint:
backbone.fpn_lateral2.{bias, weight}
backbone.fpn_lateral3.{bias, weight}
backbone.fpn_lateral4.{bias, weight}
backbone.fpn_lateral5.{bias, weight}
backbone.fpn_output2.{bias, weight}
backbone.fpn_output3.{bias, weight}
backbone.fpn_output4.{bias, weight}
backbone.fpn_output5.{bias, weight}
sem_seg_head.p2.0.norm.{bias, weight}
sem_seg_head.p2.0.weight
sem_seg_head.p3.0.norm.{bias, weight}
sem_seg_head.p3.0.weight
sem_seg_head.p4.0.norm.{bias, weight}
sem_seg_head.p4.0.weight
sem_seg_head.p4.2.norm.{bias, weight}
sem_seg_head.p4.2.weight
sem_seg_head.p5.0.norm.{bias, weight}
sem_seg_head.p5.0.weight
sem_seg_head.p5.2.norm.{bias, weight}
sem_seg_head.p5.2.weight
sem_seg_head.p5.4.norm.{bias, weight}
sem_seg_head.p5.4.weight
sem_seg_head.predictor.{bias, weight}
The checkpoint state_dict contains keys that are not used by the model:
  fc1000.{bias, weight}
  stem.conv1.bias


[06/29 04:15:19 d2.engine.train_loop]: Starting training from iteration 0
[06/29 04:15:27 d2.utils.events]:  eta: 4:28:27  iter: 19  total_loss: 4.419  time: 0.4026  data_time: 0.0228  lr: 0.00019981  max_mem: 4306M
[06/29 04:15:35 d2.utils.events]:  eta: 4:29:57  iter: 39  total_loss: 0.7295  time: 0.4050  data_time: 0.0081  lr: 0.00039961  max_mem: 4306M
[06/29 04:15:44 d2.utils.events]:  eta: 4:31:11  iter: 59  total_loss: 0.5402  time: 0.4071  data_time: 0.0076  lr: 0.00059941  max_mem: 4306M
[06/29 04:15:52 d2.utils.events]:  eta: 4:31:45  iter: 79  total_loss: 0.4211  time: 0.4089  data_time: 0.0073  lr: 0.00079921  max_mem: 4306M
[06/29 04:16:00 d2.utils.events]:  eta: 4:32:56  iter: 99  total_loss: 0.3815  time: 0.4106  data_time: 0.0073  lr: 0.00099901  max_mem: 4306M
[06/29 04:16:09 d2.utils.events]:  eta: 4:34:12  iter: 119  total_loss: 0.3794  time: 0.4122  data_time: 0.0075  lr: 0.0011988  max_mem: 4306M
[06/29 04:16:17 d2.utils.events]:  eta: 4:34:30  iter: 139  total_los

[06/29 04:23:12 d2.utils.events]:  eta: 4:39:35  iter: 1099  total_loss: 0.1397  time: 0.4293  data_time: 0.0074  lr: 0.01  max_mem: 4306M
[06/29 04:23:21 d2.utils.events]:  eta: 4:39:32  iter: 1119  total_loss: 0.1448  time: 0.4294  data_time: 0.0072  lr: 0.01  max_mem: 4306M
[06/29 04:23:29 d2.utils.events]:  eta: 4:39:28  iter: 1139  total_loss: 0.1384  time: 0.4294  data_time: 0.0079  lr: 0.01  max_mem: 4306M
[06/29 04:23:38 d2.utils.events]:  eta: 4:39:27  iter: 1159  total_loss: 0.1261  time: 0.4295  data_time: 0.0075  lr: 0.01  max_mem: 4306M
[06/29 04:23:46 d2.utils.events]:  eta: 4:39:23  iter: 1179  total_loss: 0.1303  time: 0.4295  data_time: 0.0067  lr: 0.01  max_mem: 4306M
[06/29 04:23:55 d2.utils.events]:  eta: 4:39:19  iter: 1199  total_loss: 0.1496  time: 0.4295  data_time: 0.0081  lr: 0.01  max_mem: 4306M
[06/29 04:24:04 d2.utils.events]:  eta: 4:39:17  iter: 1219  total_loss: 0.13  time: 0.4296  data_time: 0.0081  lr: 0.01  max_mem: 4306M
[06/29 04:24:13 d2.utils.even

...

[06/29 09:05:00 d2.utils.events]:  eta: 0:20:58  iter: 37039  total_loss: 0.06465  time: 0.4254  data_time: 0.0098  lr: 1e-05  max_mem: 4306M
[06/29 09:05:09 d2.utils.events]:  eta: 0:20:50  iter: 37059  total_loss: 0.0648  time: 0.4254  data_time: 0.0085  lr: 1e-05  max_mem: 4306M
[06/29 09:05:17 d2.utils.events]:  eta: 0:20:42  iter: 37079  total_loss: 0.06469  time: 0.4254  data_time: 0.0092  lr: 1e-05  max_mem: 4306M
[06/29 09:05:26 d2.utils.events]:  eta: 0:20:34  iter: 37099  total_loss: 0.06329  time: 0.4254  data_time: 0.0089  lr: 1e-05  max_mem: 4306M
[06/29 09:05:34 d2.utils.events]:  eta: 0:20:25  iter: 37119  total_loss: 0.07165  time: 0.4254  data_time: 0.0095  lr: 1e-05  max_mem: 4306M
[06/29 09:05:43 d2.utils.events]:  eta: 0:20:17  iter: 37139  total_loss: 0.06601  time: 0.4254  data_time: 0.0087  lr: 1e-05  max_mem: 4306M
[06/29 09:05:51 d2.utils.events]:  eta: 0:20:09  iter: 37159  total_loss: 0.06498  time: 0.4254  data_time: 0.0094  lr: 1e-05  max_mem: 4306M
[06/29 

[06/29 09:12:06 d2.evaluation.evaluator]: Inference done 182/1000. Dataloading: 0.0020 s/iter. Inference: 0.0473 s/iter. Eval: 0.0391 s/iter. Total: 0.0885 s/iter. ETA=0:01:12
[06/29 09:12:11 d2.evaluation.evaluator]: Inference done 240/1000. Dataloading: 0.0020 s/iter. Inference: 0.0472 s/iter. Eval: 0.0390 s/iter. Total: 0.0882 s/iter. ETA=0:01:07
[06/29 09:12:16 d2.evaluation.evaluator]: Inference done 298/1000. Dataloading: 0.0020 s/iter. Inference: 0.0471 s/iter. Eval: 0.0389 s/iter. Total: 0.0881 s/iter. ETA=0:01:01
[06/29 09:12:21 d2.evaluation.evaluator]: Inference done 355/1000. Dataloading: 0.0020 s/iter. Inference: 0.0470 s/iter. Eval: 0.0390 s/iter. Total: 0.0880 s/iter. ETA=0:00:56
[06/29 09:12:26 d2.evaluation.evaluator]: Inference done 412/1000. Dataloading: 0.0020 s/iter. Inference: 0.0469 s/iter. Eval: 0.0391 s/iter. Total: 0.0881 s/iter. ETA=0:00:51
[06/29 09:12:31 d2.evaluation.evaluator]: Inference done 467/1000. Dataloading: 0.0020 s/iter. Inference: 0.0468 s/iter.

[06/29 09:16:42 d2.utils.events]:  eta: 0:10:46  iter: 38479  total_loss: 0.06405  time: 0.4254  data_time: 0.0098  lr: 1e-06  max_mem: 4306M
[06/29 09:16:50 d2.utils.events]:  eta: 0:10:38  iter: 38499  total_loss: 0.06717  time: 0.4254  data_time: 0.0084  lr: 1e-06  max_mem: 4306M
[06/29 09:16:59 d2.utils.events]:  eta: 0:10:29  iter: 38519  total_loss: 0.06448  time: 0.4254  data_time: 0.0094  lr: 1e-06  max_mem: 4306M
[06/29 09:17:07 d2.utils.events]:  eta: 0:10:21  iter: 38539  total_loss: 0.06969  time: 0.4254  data_time: 0.0089  lr: 1e-06  max_mem: 4306M
[06/29 09:17:16 d2.utils.events]:  eta: 0:10:12  iter: 38559  total_loss: 0.07022  time: 0.4254  data_time: 0.0097  lr: 1e-06  max_mem: 4306M
[06/29 09:17:24 d2.utils.events]:  eta: 0:10:04  iter: 38579  total_loss: 0.0633  time: 0.4254  data_time: 0.0086  lr: 1e-06  max_mem: 4306M
[06/29 09:17:33 d2.utils.events]:  eta: 0:09:55  iter: 38599  total_loss: 0.0642  time: 0.4254  data_time: 0.0091  lr: 1e-06  max_mem: 4306M
[06/29 0

[06/29 09:24:30 d2.utils.events]:  eta: 0:02:58  iter: 39579  total_loss: 0.06265  time: 0.4254  data_time: 0.0083  lr: 1e-06  max_mem: 4306M
[06/29 09:24:39 d2.utils.events]:  eta: 0:02:50  iter: 39599  total_loss: 0.06307  time: 0.4254  data_time: 0.0091  lr: 1e-06  max_mem: 4306M
[06/29 09:24:47 d2.utils.events]:  eta: 0:02:41  iter: 39619  total_loss: 0.06449  time: 0.4254  data_time: 0.0093  lr: 1e-06  max_mem: 4306M
[06/29 09:24:56 d2.utils.events]:  eta: 0:02:33  iter: 39639  total_loss: 0.06554  time: 0.4254  data_time: 0.0092  lr: 1e-06  max_mem: 4306M
[06/29 09:25:04 d2.utils.events]:  eta: 0:02:24  iter: 39659  total_loss: 0.0627  time: 0.4254  data_time: 0.0094  lr: 1e-06  max_mem: 4306M
[06/29 09:25:13 d2.utils.events]:  eta: 0:02:16  iter: 39679  total_loss: 0.06575  time: 0.4254  data_time: 0.0091  lr: 1e-06  max_mem: 4306M
[06/29 09:25:21 d2.utils.events]:  eta: 0:02:07  iter: 39699  total_loss: 0.0673  time: 0.4254  data_time: 0.0087  lr: 1e-06  max_mem: 4306M
[06/29 0

[06/29 09:28:58 d2.engine.defaults]: Evaluation results for carla_night_clear_val in csv format:
[06/29 09:28:58 d2.evaluation.testing]: copypaste: Task: sem_seg
[06/29 09:28:58 d2.evaluation.testing]: copypaste: mIoU,fwIoU,mACC,pACC
[06/29 09:28:58 d2.evaluation.testing]: copypaste: 28.6803,63.4621,49.5338,77.0918


### -1. Day and Night Clear

In [29]:
trainer_all = Detectron2Trainer('combined_clear_both_train', 'combined_clear_both_val', output_folder='./output_both_clear_40k') # Actually has both day and night
trainer_all.load()
trainer_all.train()

17
[06/29 09:28:58 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/29 09:28:59 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/29 09:28:59 d2.data.build]: Using training sampler TrainingSampler
[06/29 09:28:59 d2.data.common]: Serializing 18867 elements to byte tensors and concatenating them all ...
[06/29 09:28:59 d2.data.common]: Serialized dataset takes 5.94 MiB
[06/29 09:28:59 d2.checkpoint.c2_model_loading]: Renaming Caffe2 weights ......
[06/29 09:28:59 d2.checkpoint.c2_model_loading]: Following weights matched with submodule backbone.bottom_up:
| Names in Model    | Names in Checkpoint      | Shapes                                          |
|:------------------|:-------------------------|:------------------------------------------------|
| res2.0.conv1.*    | res2_0_branch2a_{bn_*,w} | (64,) (64,) (64,) (64,) (64,64,1,1)             |
| res2.0.conv2.*    | res2_0_branch2b_{bn_*,w} | (64,) (64,) (64,) (64,) (64

Some model parameters or buffers are not found in the checkpoint:
backbone.fpn_lateral2.{bias, weight}
backbone.fpn_lateral3.{bias, weight}
backbone.fpn_lateral4.{bias, weight}
backbone.fpn_lateral5.{bias, weight}
backbone.fpn_output2.{bias, weight}
backbone.fpn_output3.{bias, weight}
backbone.fpn_output4.{bias, weight}
backbone.fpn_output5.{bias, weight}
sem_seg_head.p2.0.norm.{bias, weight}
sem_seg_head.p2.0.weight
sem_seg_head.p3.0.norm.{bias, weight}
sem_seg_head.p3.0.weight
sem_seg_head.p4.0.norm.{bias, weight}
sem_seg_head.p4.0.weight
sem_seg_head.p4.2.norm.{bias, weight}
sem_seg_head.p4.2.weight
sem_seg_head.p5.0.norm.{bias, weight}
sem_seg_head.p5.0.weight
sem_seg_head.p5.2.norm.{bias, weight}
sem_seg_head.p5.2.weight
sem_seg_head.p5.4.norm.{bias, weight}
sem_seg_head.p5.4.weight
sem_seg_head.predictor.{bias, weight}
The checkpoint state_dict contains keys that are not used by the model:
  fc1000.{bias, weight}
  stem.conv1.bias


[06/29 09:28:59 d2.engine.train_loop]: Starting training from iteration 0
[06/29 09:29:08 d2.utils.events]:  eta: 4:55:30  iter: 19  total_loss: 7.327  time: 0.4441  data_time: 0.0232  lr: 0.00019981  max_mem: 4308M
[06/29 09:29:17 d2.utils.events]:  eta: 4:40:16  iter: 39  total_loss: 0.957  time: 0.4384  data_time: 0.0082  lr: 0.00039961  max_mem: 4308M
[06/29 09:29:26 d2.utils.events]:  eta: 4:44:58  iter: 59  total_loss: 0.7235  time: 0.4448  data_time: 0.0084  lr: 0.00059941  max_mem: 4308M
[06/29 09:29:35 d2.utils.events]:  eta: 4:44:50  iter: 79  total_loss: 0.638  time: 0.4459  data_time: 0.0080  lr: 0.00079921  max_mem: 4308M
[06/29 09:29:44 d2.utils.events]:  eta: 4:43:21  iter: 99  total_loss: 0.4661  time: 0.4450  data_time: 0.0084  lr: 0.00099901  max_mem: 4308M
[06/29 09:29:52 d2.utils.events]:  eta: 4:42:53  iter: 119  total_loss: 0.3932  time: 0.4436  data_time: 0.0083  lr: 0.0011988  max_mem: 4308M
[06/29 09:30:01 d2.utils.events]:  eta: 4:42:53  iter: 139  total_loss:

[06/29 09:37:11 d2.utils.events]:  eta: 4:38:01  iter: 1099  total_loss: 0.1871  time: 0.4468  data_time: 0.0084  lr: 0.01  max_mem: 4308M
[06/29 09:37:20 d2.utils.events]:  eta: 4:37:54  iter: 1119  total_loss: 0.1795  time: 0.4466  data_time: 0.0074  lr: 0.01  max_mem: 4308M
[06/29 09:37:29 d2.utils.events]:  eta: 4:37:47  iter: 1139  total_loss: 0.1914  time: 0.4466  data_time: 0.0079  lr: 0.01  max_mem: 4308M
[06/29 09:37:38 d2.utils.events]:  eta: 4:37:35  iter: 1159  total_loss: 0.2243  time: 0.4466  data_time: 0.0082  lr: 0.01  max_mem: 4308M
[06/29 09:37:47 d2.utils.events]:  eta: 4:37:29  iter: 1179  total_loss: 0.2098  time: 0.4467  data_time: 0.0085  lr: 0.01  max_mem: 4308M
[06/29 09:37:56 d2.utils.events]:  eta: 4:37:18  iter: 1199  total_loss: 0.2109  time: 0.4467  data_time: 0.0080  lr: 0.01  max_mem: 4308M
[06/29 09:38:05 d2.utils.events]:  eta: 4:37:08  iter: 1219  total_loss: 0.2098  time: 0.4468  data_time: 0.0077  lr: 0.01  max_mem: 4308M
[06/29 09:38:14 d2.utils.ev

...

[06/29 16:53:15 d2.evaluation.sem_seg_evaluation]: OrderedDict([('sem_seg', {'mIoU': 63.90403023641426, 'fwIoU': 88.69801425805007, 'IoU-Unlabeled': nan, 'IoU-Building': 86.88199865558171, 'IoU-Fence': 39.494692492780295, 'IoU-Pedestrian': 74.3856338735606, 'IoU-Pole': 54.699730122784054, 'IoU-Road': 97.09336612452255, 'IoU-SideWalk': 80.64156460887085, 'IoU-Vegetation': 78.73239582392758, 'IoU-Vehicles': 88.33831260688063, 'IoU-Wall': 63.30375018459448, 'IoU-TrafficSign': 58.88746337794844, 'IoU-Sky': 93.08112773907958, 'IoU-TrafficLight': 61.14165920616542, 'IoU-Terrain': 55.28943955711678, 'IoU-ConstructionVehicle': 77.06005603358814, 'IoU-workzone_object': 59.20286246199061, 'IoU-Detour': 18.134461149650566, 'mACC': 77.52460378674975, 'pACC': 93.77223968150112, 'ACC-Unlabeled': nan, 'ACC-Building': 95.86024926693078, 'ACC-Fence': 56.22388667897159, 'ACC-Pedestrian': 86.22996199700013, 'ACC-Pole': 66.89668229792213, 'ACC-Road': 99.04643803032384, 'ACC-SideWalk': 86.35384631766587, '

[06/29 16:59:42 d2.utils.events]:  eta: 0:08:11  iter: 38859  total_loss: 0.07824  time: 0.4479  data_time: 0.0087  lr: 1e-06  max_mem: 4308M
[06/29 16:59:51 d2.utils.events]:  eta: 0:08:02  iter: 38879  total_loss: 0.07873  time: 0.4479  data_time: 0.0089  lr: 1e-06  max_mem: 4308M
[06/29 17:00:00 d2.utils.events]:  eta: 0:07:53  iter: 38899  total_loss: 0.0727  time: 0.4479  data_time: 0.0100  lr: 1e-06  max_mem: 4308M
[06/29 17:00:09 d2.utils.events]:  eta: 0:07:45  iter: 38919  total_loss: 0.07399  time: 0.4479  data_time: 0.0090  lr: 1e-06  max_mem: 4308M
[06/29 17:00:18 d2.utils.events]:  eta: 0:07:36  iter: 38939  total_loss: 0.07539  time: 0.4479  data_time: 0.0093  lr: 1e-06  max_mem: 4308M
[06/29 17:00:27 d2.utils.events]:  eta: 0:07:27  iter: 38959  total_loss: 0.07832  time: 0.4479  data_time: 0.0092  lr: 1e-06  max_mem: 4308M
[06/29 17:00:35 d2.utils.events]:  eta: 0:07:18  iter: 38979  total_loss: 0.08034  time: 0.4479  data_time: 0.0089  lr: 1e-06  max_mem: 4308M
[06/29 

[06/29 17:08:00 d2.utils.events]:  eta: 0:00:17  iter: 39959  total_loss: 0.0815  time: 0.4480  data_time: 0.0081  lr: 1e-06  max_mem: 4308M
[06/29 17:08:09 d2.utils.events]:  eta: 0:00:08  iter: 39979  total_loss: 0.07672  time: 0.4480  data_time: 0.0087  lr: 1e-06  max_mem: 4308M
[06/29 17:08:19 d2.utils.events]:  eta: 0:00:00  iter: 39999  total_loss: 0.08045  time: 0.4480  data_time: 0.0088  lr: 1e-06  max_mem: 4308M
[06/29 17:08:19 d2.engine.hooks]: Overall training speed: 39998 iterations in 4:58:40 (0.4480 s / it)
[06/29 17:08:19 d2.engine.hooks]: Total training time: 7:39:18 (2:40:37 on hooks)
[06/29 17:08:19 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in inference: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice')]
[06/29 17:08:19 d2.data.common]: Serializing 4957 elements to byte tensors and concatenating them all ...
[06/29 17:08:19 d2.data.common]: Serialized dataset takes 1.52 MiB
[06/29 17:08:19 d2.evaluation.evaluator

[06/29 17:11:36 d2.evaluation.evaluator]: Inference done 2317/4957. Dataloading: 0.0021 s/iter. Inference: 0.0469 s/iter. Eval: 0.0362 s/iter. Total: 0.0852 s/iter. ETA=0:03:44
[06/29 17:11:41 d2.evaluation.evaluator]: Inference done 2375/4957. Dataloading: 0.0021 s/iter. Inference: 0.0469 s/iter. Eval: 0.0362 s/iter. Total: 0.0853 s/iter. ETA=0:03:40
[06/29 17:11:46 d2.evaluation.evaluator]: Inference done 2432/4957. Dataloading: 0.0021 s/iter. Inference: 0.0469 s/iter. Eval: 0.0363 s/iter. Total: 0.0853 s/iter. ETA=0:03:35
[06/29 17:11:51 d2.evaluation.evaluator]: Inference done 2489/4957. Dataloading: 0.0021 s/iter. Inference: 0.0469 s/iter. Eval: 0.0363 s/iter. Total: 0.0854 s/iter. ETA=0:03:30
[06/29 17:11:57 d2.evaluation.evaluator]: Inference done 2548/4957. Dataloading: 0.0021 s/iter. Inference: 0.0469 s/iter. Eval: 0.0363 s/iter. Total: 0.0854 s/iter. ETA=0:03:25
[06/29 17:12:02 d2.evaluation.evaluator]: Inference done 2607/4957. Dataloading: 0.0021 s/iter. Inference: 0.0469 s

[06/29 17:15:25 d2.evaluation.evaluator]: Inference done 4039/4957. Dataloading: 0.0021 s/iter. Inference: 0.0487 s/iter. Eval: 0.0546 s/iter. Total: 0.1056 s/iter. ETA=0:01:36
[06/29 17:15:30 d2.evaluation.evaluator]: Inference done 4096/4957. Dataloading: 0.0021 s/iter. Inference: 0.0487 s/iter. Eval: 0.0544 s/iter. Total: 0.1053 s/iter. ETA=0:01:30
[06/29 17:15:35 d2.evaluation.evaluator]: Inference done 4154/4957. Dataloading: 0.0021 s/iter. Inference: 0.0487 s/iter. Eval: 0.0542 s/iter. Total: 0.1051 s/iter. ETA=0:01:24
[06/29 17:15:40 d2.evaluation.evaluator]: Inference done 4212/4957. Dataloading: 0.0021 s/iter. Inference: 0.0486 s/iter. Eval: 0.0540 s/iter. Total: 0.1048 s/iter. ETA=0:01:18
[06/29 17:15:45 d2.evaluation.evaluator]: Inference done 4269/4957. Dataloading: 0.0021 s/iter. Inference: 0.0486 s/iter. Eval: 0.0538 s/iter. Total: 0.1046 s/iter. ETA=0:01:11
[06/29 17:15:50 d2.evaluation.evaluator]: Inference done 4326/4957. Dataloading: 0.0022 s/iter. Inference: 0.0486 s

### 1. Day

In [30]:
trainer_all = Detectron2Trainer('combined_all_train', 'combined_all_val', output_folder='./output_day_40k')
trainer_all.load()
trainer_all.train()

17
[06/29 17:16:46 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/29 17:16:46 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/29 17:16:46 d2.data.build]: Using training sampler TrainingSampler
[06/29 17:16:46 d2.data.common]: Serializing 22288 elements to byte tensors and concatenating them all ...
[06/29 17:16:46 d2.data.common]: Serialized dataset takes 6.80 MiB
[06/29 17:16:46 d2.checkpoint.c2_model_loading]: Renaming Caffe2 weights ......
[06/29 17:16:46 d2.checkpoint.c2_model_loading]: Following weights matched with submodule backbone.bottom_up:
| Names in Model    | Names in Checkpoint      | Shapes                                          |
|:------------------|:-------------------------|:------------------------------------------------|
| res2.0.conv1.*    | res2_0_branch2a_{bn_*,w} | (64,) (64,) (64,) (64,) (64,64,1,1)             |
| res2.0.conv2.*    | res2_0_branch2b_{bn_*,w} | (64,) (64,) (64,) (64,) (64

Some model parameters or buffers are not found in the checkpoint:
backbone.fpn_lateral2.{bias, weight}
backbone.fpn_lateral3.{bias, weight}
backbone.fpn_lateral4.{bias, weight}
backbone.fpn_lateral5.{bias, weight}
backbone.fpn_output2.{bias, weight}
backbone.fpn_output3.{bias, weight}
backbone.fpn_output4.{bias, weight}
backbone.fpn_output5.{bias, weight}
sem_seg_head.p2.0.norm.{bias, weight}
sem_seg_head.p2.0.weight
sem_seg_head.p3.0.norm.{bias, weight}
sem_seg_head.p3.0.weight
sem_seg_head.p4.0.norm.{bias, weight}
sem_seg_head.p4.0.weight
sem_seg_head.p4.2.norm.{bias, weight}
sem_seg_head.p4.2.weight
sem_seg_head.p5.0.norm.{bias, weight}
sem_seg_head.p5.0.weight
sem_seg_head.p5.2.norm.{bias, weight}
sem_seg_head.p5.2.weight
sem_seg_head.p5.4.norm.{bias, weight}
sem_seg_head.p5.4.weight
sem_seg_head.predictor.{bias, weight}
The checkpoint state_dict contains keys that are not used by the model:
  fc1000.{bias, weight}
  stem.conv1.bias


[06/29 17:16:46 d2.engine.train_loop]: Starting training from iteration 0
[06/29 17:16:56 d2.utils.events]:  eta: 5:16:33  iter: 19  total_loss: 4.607  time: 0.4547  data_time: 0.0283  lr: 0.00019981  max_mem: 4308M
[06/29 17:17:05 d2.utils.events]:  eta: 4:58:17  iter: 39  total_loss: 1.035  time: 0.4477  data_time: 0.0087  lr: 0.00039961  max_mem: 4308M
[06/29 17:17:14 d2.utils.events]:  eta: 4:45:15  iter: 59  total_loss: 0.6187  time: 0.4456  data_time: 0.0085  lr: 0.00059941  max_mem: 4308M
[06/29 17:17:23 d2.utils.events]:  eta: 5:09:40  iter: 79  total_loss: 0.5703  time: 0.4483  data_time: 0.0092  lr: 0.00079921  max_mem: 4308M
[06/29 17:17:32 d2.utils.events]:  eta: 5:11:35  iter: 99  total_loss: 0.4236  time: 0.4505  data_time: 0.0080  lr: 0.00099901  max_mem: 4308M
[06/29 17:17:41 d2.utils.events]:  eta: 5:11:01  iter: 119  total_loss: 0.423  time: 0.4509  data_time: 0.0086  lr: 0.0011988  max_mem: 4308M
[06/29 17:17:50 d2.utils.events]:  eta: 5:10:51  iter: 139  total_loss:

[06/29 17:25:14 d2.utils.events]:  eta: 5:10:17  iter: 1099  total_loss: 0.1947  time: 0.4604  data_time: 0.0075  lr: 0.01  max_mem: 4308M
[06/29 17:25:23 d2.utils.events]:  eta: 5:10:13  iter: 1119  total_loss: 0.1693  time: 0.4605  data_time: 0.0079  lr: 0.01  max_mem: 4308M
[06/29 17:25:32 d2.utils.events]:  eta: 5:10:09  iter: 1139  total_loss: 0.1688  time: 0.4604  data_time: 0.0082  lr: 0.01  max_mem: 4308M
[06/29 17:25:41 d2.utils.events]:  eta: 5:10:00  iter: 1159  total_loss: 0.1781  time: 0.4603  data_time: 0.0078  lr: 0.01  max_mem: 4308M
[06/29 17:25:51 d2.utils.events]:  eta: 5:10:00  iter: 1179  total_loss: 0.1944  time: 0.4605  data_time: 0.0086  lr: 0.01  max_mem: 4308M
[06/29 17:26:00 d2.utils.events]:  eta: 5:10:03  iter: 1199  total_loss: 0.1909  time: 0.4606  data_time: 0.0089  lr: 0.01  max_mem: 4308M
[06/29 17:26:09 d2.utils.events]:  eta: 5:09:50  iter: 1219  total_loss: 0.192  time: 0.4606  data_time: 0.0097  lr: 0.01  max_mem: 4308M
[06/29 17:26:19 d2.utils.eve

...

[06/29 23:36:20 d2.evaluation.evaluator]: Inference done 1059/2000. Dataloading: 0.0020 s/iter. Inference: 0.0473 s/iter. Eval: 0.0421 s/iter. Total: 0.0914 s/iter. ETA=0:01:26
[06/29 23:36:25 d2.evaluation.evaluator]: Inference done 1084/2000. Dataloading: 0.0020 s/iter. Inference: 0.0475 s/iter. Eval: 0.0444 s/iter. Total: 0.0940 s/iter. ETA=0:01:26
[06/29 23:36:30 d2.evaluation.evaluator]: Inference done 1108/2000. Dataloading: 0.0020 s/iter. Inference: 0.0477 s/iter. Eval: 0.0467 s/iter. Total: 0.0966 s/iter. ETA=0:01:26
[06/29 23:36:35 d2.evaluation.evaluator]: Inference done 1133/2000. Dataloading: 0.0020 s/iter. Inference: 0.0480 s/iter. Eval: 0.0489 s/iter. Total: 0.0989 s/iter. ETA=0:01:25
[06/29 23:36:40 d2.evaluation.evaluator]: Inference done 1158/2000. Dataloading: 0.0020 s/iter. Inference: 0.0482 s/iter. Eval: 0.0510 s/iter. Total: 0.1013 s/iter. ETA=0:01:25
[06/29 23:36:45 d2.evaluation.evaluator]: Inference done 1183/2000. Dataloading: 0.0020 s/iter. Inference: 0.0484 s

[06/29 23:39:33 d2.engine.defaults]: Evaluation results for combined_all_val in csv format:
[06/29 23:39:33 d2.evaluation.testing]: copypaste: Task: sem_seg
[06/29 23:39:33 d2.evaluation.testing]: copypaste: mIoU,fwIoU,mACC,pACC
[06/29 23:39:33 d2.evaluation.testing]: copypaste: 63.0227,91.6454,84.9930,95.4867
[06/29 23:39:33 d2.utils.events]:  eta: 0:15:55  iter: 37999  total_loss: 0.0728  time: 0.4580  data_time: 0.0070  lr: 1e-05  max_mem: 4308M
[06/29 23:39:42 d2.utils.events]:  eta: 0:15:45  iter: 38019  total_loss: 0.07932  time: 0.4580  data_time: 0.0081  lr: 1e-06  max_mem: 4308M
[06/29 23:39:50 d2.utils.events]:  eta: 0:15:34  iter: 38039  total_loss: 0.08374  time: 0.4580  data_time: 0.0081  lr: 1e-06  max_mem: 4308M
[06/29 23:39:59 d2.utils.events]:  eta: 0:15:24  iter: 38059  total_loss: 0.0798  time: 0.4580  data_time: 0.0078  lr: 1e-06  max_mem: 4308M
[06/29 23:40:08 d2.utils.events]:  eta: 0:15:13  iter: 38079  total_loss: 0.08733  time: 0.4580  data_time: 0.0071  lr: 1e

[06/29 23:47:37 d2.utils.events]:  eta: 0:07:24  iter: 39059  total_loss: 0.07447  time: 0.4580  data_time: 0.0089  lr: 1e-06  max_mem: 4308M
[06/29 23:47:46 d2.utils.events]:  eta: 0:07:15  iter: 39079  total_loss: 0.08471  time: 0.4580  data_time: 0.0091  lr: 1e-06  max_mem: 4308M
[06/29 23:47:55 d2.utils.events]:  eta: 0:07:06  iter: 39099  total_loss: 0.07284  time: 0.4580  data_time: 0.0087  lr: 1e-06  max_mem: 4308M
[06/29 23:48:04 d2.utils.events]:  eta: 0:06:57  iter: 39119  total_loss: 0.072  time: 0.4580  data_time: 0.0089  lr: 1e-06  max_mem: 4308M
[06/29 23:48:14 d2.utils.events]:  eta: 0:06:48  iter: 39139  total_loss: 0.07608  time: 0.4580  data_time: 0.0087  lr: 1e-06  max_mem: 4308M
[06/29 23:48:23 d2.utils.events]:  eta: 0:06:39  iter: 39159  total_loss: 0.07824  time: 0.4580  data_time: 0.0090  lr: 1e-06  max_mem: 4308M
[06/29 23:48:32 d2.utils.events]:  eta: 0:06:30  iter: 39179  total_loss: 0.08091  time: 0.4580  data_time: 0.0087  lr: 1e-06  max_mem: 4308M
[06/29 2

[06/29 23:55:03 d2.evaluation.evaluator]: Inference done 126/2000. Dataloading: 0.0021 s/iter. Inference: 0.0472 s/iter. Eval: 0.0387 s/iter. Total: 0.0881 s/iter. ETA=0:02:45
[06/29 23:55:08 d2.evaluation.evaluator]: Inference done 185/2000. Dataloading: 0.0021 s/iter. Inference: 0.0471 s/iter. Eval: 0.0377 s/iter. Total: 0.0870 s/iter. ETA=0:02:37
[06/29 23:55:13 d2.evaluation.evaluator]: Inference done 245/2000. Dataloading: 0.0021 s/iter. Inference: 0.0471 s/iter. Eval: 0.0371 s/iter. Total: 0.0864 s/iter. ETA=0:02:31
[06/29 23:55:18 d2.evaluation.evaluator]: Inference done 305/2000. Dataloading: 0.0021 s/iter. Inference: 0.0471 s/iter. Eval: 0.0367 s/iter. Total: 0.0859 s/iter. ETA=0:02:25
[06/29 23:55:23 d2.evaluation.evaluator]: Inference done 364/2000. Dataloading: 0.0021 s/iter. Inference: 0.0470 s/iter. Eval: 0.0365 s/iter. Total: 0.0857 s/iter. ETA=0:02:20
[06/29 23:55:28 d2.evaluation.evaluator]: Inference done 424/2000. Dataloading: 0.0021 s/iter. Inference: 0.0470 s/iter.

[06/29 23:58:52 d2.evaluation.evaluator]: Inference done 1757/2000. Dataloading: 0.0023 s/iter. Inference: 0.0514 s/iter. Eval: 0.0830 s/iter. Total: 0.1367 s/iter. ETA=0:00:33
[06/29 23:58:57 d2.evaluation.evaluator]: Inference done 1781/2000. Dataloading: 0.0023 s/iter. Inference: 0.0514 s/iter. Eval: 0.0839 s/iter. Total: 0.1377 s/iter. ETA=0:00:30
[06/29 23:59:02 d2.evaluation.evaluator]: Inference done 1805/2000. Dataloading: 0.0023 s/iter. Inference: 0.0515 s/iter. Eval: 0.0848 s/iter. Total: 0.1387 s/iter. ETA=0:00:27
[06/29 23:59:07 d2.evaluation.evaluator]: Inference done 1830/2000. Dataloading: 0.0023 s/iter. Inference: 0.0516 s/iter. Eval: 0.0856 s/iter. Total: 0.1396 s/iter. ETA=0:00:23
[06/29 23:59:12 d2.evaluation.evaluator]: Inference done 1855/2000. Dataloading: 0.0023 s/iter. Inference: 0.0517 s/iter. Eval: 0.0864 s/iter. Total: 0.1404 s/iter. ETA=0:00:20
[06/29 23:59:17 d2.evaluation.evaluator]: Inference done 1880/2000. Dataloading: 0.0023 s/iter. Inference: 0.0518 s

### 2. Night

In [32]:
trainer_all = Detectron2Trainer('carla_night_all_train', 'carla_night_all_val', output_folder='./output_night_40k')
trainer_all.load()
trainer_all.train()

17
[06/30 01:53:58 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/30 01:53:58 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/30 01:53:58 d2.data.build]: Using training sampler TrainingSampler
[06/30 01:53:58 d2.data.common]: Serializing 15446 elements to byte tensors and concatenating them all ...
[06/30 01:53:59 d2.data.common]: Serialized dataset takes 5.05 MiB
[06/30 01:53:59 d2.checkpoint.c2_model_loading]: Renaming Caffe2 weights ......
[06/30 01:53:59 d2.checkpoint.c2_model_loading]: Following weights matched with submodule backbone.bottom_up:
| Names in Model    | Names in Checkpoint      | Shapes                                          |
|:------------------|:-------------------------|:------------------------------------------------|
| res2.0.conv1.*    | res2_0_branch2a_{bn_*,w} | (64,) (64,) (64,) (64,) (64,64,1,1)             |
| res2.0.conv2.*    | res2_0_branch2b_{bn_*,w} | (64,) (64,) (64,) (64,) (64

Some model parameters or buffers are not found in the checkpoint:
backbone.fpn_lateral2.{bias, weight}
backbone.fpn_lateral3.{bias, weight}
backbone.fpn_lateral4.{bias, weight}
backbone.fpn_lateral5.{bias, weight}
backbone.fpn_output2.{bias, weight}
backbone.fpn_output3.{bias, weight}
backbone.fpn_output4.{bias, weight}
backbone.fpn_output5.{bias, weight}
sem_seg_head.p2.0.norm.{bias, weight}
sem_seg_head.p2.0.weight
sem_seg_head.p3.0.norm.{bias, weight}
sem_seg_head.p3.0.weight
sem_seg_head.p4.0.norm.{bias, weight}
sem_seg_head.p4.0.weight
sem_seg_head.p4.2.norm.{bias, weight}
sem_seg_head.p4.2.weight
sem_seg_head.p5.0.norm.{bias, weight}
sem_seg_head.p5.0.weight
sem_seg_head.p5.2.norm.{bias, weight}
sem_seg_head.p5.2.weight
sem_seg_head.p5.4.norm.{bias, weight}
sem_seg_head.p5.4.weight
sem_seg_head.predictor.{bias, weight}
The checkpoint state_dict contains keys that are not used by the model:
  fc1000.{bias, weight}
  stem.conv1.bias


[06/30 01:53:59 d2.engine.train_loop]: Starting training from iteration 0
[06/30 01:54:07 d2.utils.events]:  eta: 4:29:29  iter: 19  total_loss: 5.256  time: 0.4040  data_time: 0.0244  lr: 0.00019981  max_mem: 4308M
[06/30 01:54:15 d2.utils.events]:  eta: 4:29:32  iter: 39  total_loss: 0.946  time: 0.4045  data_time: 0.0084  lr: 0.00039961  max_mem: 4308M
[06/30 01:54:23 d2.utils.events]:  eta: 4:29:33  iter: 59  total_loss: 0.5756  time: 0.4046  data_time: 0.0084  lr: 0.00059941  max_mem: 4308M
[06/30 01:54:32 d2.utils.events]:  eta: 4:29:59  iter: 79  total_loss: 0.5646  time: 0.4054  data_time: 0.0081  lr: 0.00079921  max_mem: 4308M
[06/30 01:54:40 d2.utils.events]:  eta: 4:30:30  iter: 99  total_loss: 0.4623  time: 0.4064  data_time: 0.0088  lr: 0.00099901  max_mem: 4308M
[06/30 01:54:48 d2.utils.events]:  eta: 4:30:42  iter: 119  total_loss: 0.4742  time: 0.4070  data_time: 0.0082  lr: 0.0011988  max_mem: 4308M
[06/30 01:54:56 d2.utils.events]:  eta: 4:30:08  iter: 139  total_loss

[06/30 02:01:37 d2.utils.events]:  eta: 4:30:41  iter: 1099  total_loss: 0.1894  time: 0.4161  data_time: 0.0077  lr: 0.01  max_mem: 4308M
[06/30 02:01:46 d2.utils.events]:  eta: 4:30:40  iter: 1119  total_loss: 0.1768  time: 0.4162  data_time: 0.0076  lr: 0.01  max_mem: 4308M
[06/30 02:01:54 d2.utils.events]:  eta: 4:30:48  iter: 1139  total_loss: 0.1579  time: 0.4163  data_time: 0.0072  lr: 0.01  max_mem: 4308M
[06/30 02:02:03 d2.utils.events]:  eta: 4:30:45  iter: 1159  total_loss: 0.1712  time: 0.4164  data_time: 0.0068  lr: 0.01  max_mem: 4308M
[06/30 02:02:11 d2.utils.events]:  eta: 4:30:42  iter: 1179  total_loss: 0.1634  time: 0.4164  data_time: 0.0072  lr: 0.01  max_mem: 4308M
[06/30 02:02:20 d2.utils.events]:  eta: 4:30:43  iter: 1199  total_loss: 0.1518  time: 0.4165  data_time: 0.0070  lr: 0.01  max_mem: 4308M
[06/30 02:02:28 d2.utils.events]:  eta: 4:30:42  iter: 1219  total_loss: 0.1613  time: 0.4166  data_time: 0.0075  lr: 0.01  max_mem: 4308M
[06/30 02:02:36 d2.utils.ev

...

[06/30 07:11:32 d2.utils.events]:  eta: 0:18:18  iter: 37419  total_loss: 0.07716  time: 0.4248  data_time: 0.0089  lr: 1e-05  max_mem: 4308M
[06/30 07:11:40 d2.utils.events]:  eta: 0:18:10  iter: 37439  total_loss: 0.07776  time: 0.4248  data_time: 0.0088  lr: 1e-05  max_mem: 4308M
[06/30 07:11:49 d2.utils.events]:  eta: 0:18:01  iter: 37459  total_loss: 0.07546  time: 0.4248  data_time: 0.0092  lr: 1e-05  max_mem: 4308M
[06/30 07:11:57 d2.utils.events]:  eta: 0:17:53  iter: 37479  total_loss: 0.0756  time: 0.4248  data_time: 0.0091  lr: 1e-05  max_mem: 4308M
[06/30 07:12:06 d2.utils.events]:  eta: 0:17:44  iter: 37499  total_loss: 0.07346  time: 0.4248  data_time: 0.0093  lr: 1e-05  max_mem: 4308M
[06/30 07:12:14 d2.utils.events]:  eta: 0:17:35  iter: 37519  total_loss: 0.07287  time: 0.4248  data_time: 0.0084  lr: 1e-05  max_mem: 4308M
[06/30 07:12:23 d2.utils.events]:  eta: 0:17:26  iter: 37539  total_loss: 0.07678  time: 0.4248  data_time: 0.0082  lr: 1e-05  max_mem: 4308M
[06/30 

[06/30 07:17:16 d2.evaluation.evaluator]: Inference done 1111/2000. Dataloading: 0.0021 s/iter. Inference: 0.0466 s/iter. Eval: 0.0383 s/iter. Total: 0.0871 s/iter. ETA=0:01:17
[06/30 07:17:21 d2.evaluation.evaluator]: Inference done 1170/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0383 s/iter. Total: 0.0870 s/iter. ETA=0:01:12
[06/30 07:17:26 d2.evaluation.evaluator]: Inference done 1228/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0383 s/iter. Total: 0.0870 s/iter. ETA=0:01:07
[06/30 07:17:31 d2.evaluation.evaluator]: Inference done 1287/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0383 s/iter. Total: 0.0870 s/iter. ETA=0:01:02
[06/30 07:17:36 d2.evaluation.evaluator]: Inference done 1345/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0383 s/iter. Total: 0.0870 s/iter. ETA=0:00:56
[06/30 07:17:41 d2.evaluation.evaluator]: Inference done 1403/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s

[06/30 07:21:40 d2.utils.events]:  eta: 0:11:02  iter: 38439  total_loss: 0.07276  time: 0.4247  data_time: 0.0090  lr: 1e-06  max_mem: 4308M
[06/30 07:21:48 d2.utils.events]:  eta: 0:10:54  iter: 38459  total_loss: 0.06829  time: 0.4247  data_time: 0.0090  lr: 1e-06  max_mem: 4308M
[06/30 07:21:57 d2.utils.events]:  eta: 0:10:45  iter: 38479  total_loss: 0.06912  time: 0.4248  data_time: 0.0089  lr: 1e-06  max_mem: 4308M
[06/30 07:22:06 d2.utils.events]:  eta: 0:10:36  iter: 38499  total_loss: 0.07879  time: 0.4248  data_time: 0.0087  lr: 1e-06  max_mem: 4308M
[06/30 07:22:14 d2.utils.events]:  eta: 0:10:28  iter: 38519  total_loss: 0.0755  time: 0.4248  data_time: 0.0083  lr: 1e-06  max_mem: 4308M
[06/30 07:22:23 d2.utils.events]:  eta: 0:10:20  iter: 38539  total_loss: 0.07716  time: 0.4247  data_time: 0.0086  lr: 1e-06  max_mem: 4308M
[06/30 07:22:31 d2.utils.events]:  eta: 0:10:11  iter: 38559  total_loss: 0.07806  time: 0.4247  data_time: 0.0085  lr: 1e-06  max_mem: 4308M
[06/30 

[06/30 07:29:29 d2.utils.events]:  eta: 0:03:15  iter: 39539  total_loss: 0.07431  time: 0.4248  data_time: 0.0092  lr: 1e-06  max_mem: 4308M
[06/30 07:29:38 d2.utils.events]:  eta: 0:03:07  iter: 39559  total_loss: 0.07765  time: 0.4248  data_time: 0.0093  lr: 1e-06  max_mem: 4308M
[06/30 07:29:46 d2.utils.events]:  eta: 0:02:58  iter: 39579  total_loss: 0.0726  time: 0.4248  data_time: 0.0092  lr: 1e-06  max_mem: 4308M
[06/30 07:29:55 d2.utils.events]:  eta: 0:02:50  iter: 39599  total_loss: 0.07133  time: 0.4248  data_time: 0.0095  lr: 1e-06  max_mem: 4308M
[06/30 07:30:03 d2.utils.events]:  eta: 0:02:41  iter: 39619  total_loss: 0.07435  time: 0.4248  data_time: 0.0081  lr: 1e-06  max_mem: 4308M
[06/30 07:30:12 d2.utils.events]:  eta: 0:02:33  iter: 39639  total_loss: 0.071  time: 0.4248  data_time: 0.0090  lr: 1e-06  max_mem: 4308M
[06/30 07:30:20 d2.utils.events]:  eta: 0:02:24  iter: 39659  total_loss: 0.07119  time: 0.4248  data_time: 0.0089  lr: 1e-06  max_mem: 4308M
[06/30 07

[06/30 07:34:38 d2.evaluation.evaluator]: Inference done 1299/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0375 s/iter. Total: 0.0861 s/iter. ETA=0:01:00
[06/30 07:34:43 d2.evaluation.evaluator]: Inference done 1358/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0375 s/iter. Total: 0.0861 s/iter. ETA=0:00:55
[06/30 07:34:48 d2.evaluation.evaluator]: Inference done 1417/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0374 s/iter. Total: 0.0861 s/iter. ETA=0:00:50
[06/30 07:34:53 d2.evaluation.evaluator]: Inference done 1474/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0375 s/iter. Total: 0.0862 s/iter. ETA=0:00:45
[06/30 07:34:58 d2.evaluation.evaluator]: Inference done 1532/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s/iter. Eval: 0.0376 s/iter. Total: 0.0862 s/iter. ETA=0:00:40
[06/30 07:35:03 d2.evaluation.evaluator]: Inference done 1590/2000. Dataloading: 0.0021 s/iter. Inference: 0.0465 s

### 3. Day and Night

In [33]:
trainer_all = Detectron2Trainer('combined_all_night_train', 'combined_all_night_val', output_folder='./output_both_40k') # Actually has both day and night
trainer_all.load()
trainer_all.train()

17
[06/30 07:35:39 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/30 07:35:39 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/30 07:35:39 d2.data.build]: Using training sampler TrainingSampler
[06/30 07:35:39 d2.data.common]: Serializing 37734 elements to byte tensors and concatenating them all ...
[06/30 07:35:39 d2.data.common]: Serialized dataset takes 11.85 MiB
[06/30 07:35:39 d2.checkpoint.c2_model_loading]: Renaming Caffe2 weights ......
[06/30 07:35:39 d2.checkpoint.c2_model_loading]: Following weights matched with submodule backbone.bottom_up:
| Names in Model    | Names in Checkpoint      | Shapes                                          |
|:------------------|:-------------------------|:------------------------------------------------|
| res2.0.conv1.*    | res2_0_branch2a_{bn_*,w} | (64,) (64,) (64,) (64,) (64,64,1,1)             |
| res2.0.conv2.*    | res2_0_branch2b_{bn_*,w} | (64,) (64,) (64,) (64,) (6

Some model parameters or buffers are not found in the checkpoint:
backbone.fpn_lateral2.{bias, weight}
backbone.fpn_lateral3.{bias, weight}
backbone.fpn_lateral4.{bias, weight}
backbone.fpn_lateral5.{bias, weight}
backbone.fpn_output2.{bias, weight}
backbone.fpn_output3.{bias, weight}
backbone.fpn_output4.{bias, weight}
backbone.fpn_output5.{bias, weight}
sem_seg_head.p2.0.norm.{bias, weight}
sem_seg_head.p2.0.weight
sem_seg_head.p3.0.norm.{bias, weight}
sem_seg_head.p3.0.weight
sem_seg_head.p4.0.norm.{bias, weight}
sem_seg_head.p4.0.weight
sem_seg_head.p4.2.norm.{bias, weight}
sem_seg_head.p4.2.weight
sem_seg_head.p5.0.norm.{bias, weight}
sem_seg_head.p5.0.weight
sem_seg_head.p5.2.norm.{bias, weight}
sem_seg_head.p5.2.weight
sem_seg_head.p5.4.norm.{bias, weight}
sem_seg_head.p5.4.weight
sem_seg_head.predictor.{bias, weight}
The checkpoint state_dict contains keys that are not used by the model:
  fc1000.{bias, weight}
  stem.conv1.bias


[06/30 07:35:39 d2.engine.train_loop]: Starting training from iteration 0
[06/30 07:35:49 d2.utils.events]:  eta: 4:53:29  iter: 19  total_loss: 3.619  time: 0.4425  data_time: 0.0232  lr: 0.00019981  max_mem: 4308M
[06/30 07:35:57 d2.utils.events]:  eta: 4:41:49  iter: 39  total_loss: 0.8268  time: 0.4412  data_time: 0.0081  lr: 0.00039961  max_mem: 4308M
[06/30 07:36:06 d2.utils.events]:  eta: 4:41:33  iter: 59  total_loss: 0.6027  time: 0.4384  data_time: 0.0086  lr: 0.00059941  max_mem: 4308M
[06/30 07:36:15 d2.utils.events]:  eta: 4:41:30  iter: 79  total_loss: 0.5183  time: 0.4412  data_time: 0.0087  lr: 0.00079921  max_mem: 4308M
[06/30 07:36:24 d2.utils.events]:  eta: 4:42:08  iter: 99  total_loss: 0.4911  time: 0.4430  data_time: 0.0089  lr: 0.00099901  max_mem: 4308M
[06/30 07:36:33 d2.utils.events]:  eta: 4:42:11  iter: 119  total_loss: 0.4408  time: 0.4424  data_time: 0.0081  lr: 0.0011988  max_mem: 4308M
[06/30 07:36:42 d2.utils.events]:  eta: 4:42:48  iter: 139  total_los

[06/30 07:43:52 d2.utils.events]:  eta: 4:38:10  iter: 1099  total_loss: 0.2699  time: 0.4469  data_time: 0.0075  lr: 0.01  max_mem: 4308M
[06/30 07:44:01 d2.utils.events]:  eta: 4:38:05  iter: 1119  total_loss: 0.2681  time: 0.4468  data_time: 0.0082  lr: 0.01  max_mem: 4308M
[06/30 07:44:10 d2.utils.events]:  eta: 4:38:03  iter: 1139  total_loss: 0.2232  time: 0.4469  data_time: 0.0079  lr: 0.01  max_mem: 4308M
[06/30 07:44:19 d2.utils.events]:  eta: 4:37:53  iter: 1159  total_loss: 0.2462  time: 0.4469  data_time: 0.0083  lr: 0.01  max_mem: 4308M
[06/30 07:44:28 d2.utils.events]:  eta: 4:37:37  iter: 1179  total_loss: 0.2121  time: 0.4468  data_time: 0.0075  lr: 0.01  max_mem: 4308M
[06/30 07:44:37 d2.utils.events]:  eta: 4:37:28  iter: 1199  total_loss: 0.2092  time: 0.4469  data_time: 0.0080  lr: 0.01  max_mem: 4308M
[06/30 07:44:46 d2.utils.events]:  eta: 4:37:20  iter: 1219  total_loss: 0.283  time: 0.4469  data_time: 0.0079  lr: 0.01  max_mem: 4308M
[06/30 07:44:54 d2.utils.eve

...

[06/30 14:14:28 d2.evaluation.evaluator]: Inference done 1817/3000. Dataloading: 0.0021 s/iter. Inference: 0.0516 s/iter. Eval: 0.0814 s/iter. Total: 0.1351 s/iter. ETA=0:02:39
[06/30 14:14:33 d2.evaluation.evaluator]: Inference done 1843/3000. Dataloading: 0.0021 s/iter. Inference: 0.0516 s/iter. Eval: 0.0822 s/iter. Total: 0.1359 s/iter. ETA=0:02:37
[06/30 14:14:38 d2.evaluation.evaluator]: Inference done 1869/3000. Dataloading: 0.0021 s/iter. Inference: 0.0517 s/iter. Eval: 0.0829 s/iter. Total: 0.1368 s/iter. ETA=0:02:34
[06/30 14:14:43 d2.evaluation.evaluator]: Inference done 1895/3000. Dataloading: 0.0021 s/iter. Inference: 0.0518 s/iter. Eval: 0.0836 s/iter. Total: 0.1376 s/iter. ETA=0:02:32
[06/30 14:14:48 d2.evaluation.evaluator]: Inference done 1921/3000. Dataloading: 0.0021 s/iter. Inference: 0.0519 s/iter. Eval: 0.0843 s/iter. Total: 0.1384 s/iter. ETA=0:02:29
[06/30 14:14:53 d2.evaluation.evaluator]: Inference done 1948/3000. Dataloading: 0.0021 s/iter. Inference: 0.0520 s

[06/30 14:18:09 d2.utils.events]:  eta: 0:12:46  iter: 38219  total_loss: 0.07989  time: 0.4471  data_time: 0.0080  lr: 1e-06  max_mem: 4308M
[06/30 14:18:18 d2.utils.events]:  eta: 0:12:38  iter: 38239  total_loss: 0.0874  time: 0.4471  data_time: 0.0074  lr: 1e-06  max_mem: 4308M
[06/30 14:18:27 d2.utils.events]:  eta: 0:12:29  iter: 38259  total_loss: 0.08618  time: 0.4471  data_time: 0.0076  lr: 1e-06  max_mem: 4308M
[06/30 14:18:36 d2.utils.events]:  eta: 0:12:20  iter: 38279  total_loss: 0.07802  time: 0.4471  data_time: 0.0070  lr: 1e-06  max_mem: 4308M
[06/30 14:18:45 d2.utils.events]:  eta: 0:12:11  iter: 38299  total_loss: 0.08311  time: 0.4471  data_time: 0.0068  lr: 1e-06  max_mem: 4308M
[06/30 14:18:54 d2.utils.events]:  eta: 0:12:03  iter: 38319  total_loss: 0.08477  time: 0.4471  data_time: 0.0069  lr: 1e-06  max_mem: 4308M
[06/30 14:19:03 d2.utils.events]:  eta: 0:11:54  iter: 38339  total_loss: 0.07876  time: 0.4471  data_time: 0.0083  lr: 1e-06  max_mem: 4308M
[06/30 

[06/30 14:26:23 d2.utils.events]:  eta: 0:04:52  iter: 39319  total_loss: 0.08588  time: 0.4471  data_time: 0.0077  lr: 1e-06  max_mem: 4308M
[06/30 14:26:31 d2.utils.events]:  eta: 0:04:43  iter: 39339  total_loss: 0.07841  time: 0.4471  data_time: 0.0075  lr: 1e-06  max_mem: 4308M
[06/30 14:26:40 d2.utils.events]:  eta: 0:04:35  iter: 39359  total_loss: 0.09168  time: 0.4471  data_time: 0.0079  lr: 1e-06  max_mem: 4308M
[06/30 14:26:49 d2.utils.events]:  eta: 0:04:26  iter: 39379  total_loss: 0.07904  time: 0.4471  data_time: 0.0078  lr: 1e-06  max_mem: 4308M
[06/30 14:26:59 d2.utils.events]:  eta: 0:04:17  iter: 39399  total_loss: 0.08022  time: 0.4472  data_time: 0.0078  lr: 1e-06  max_mem: 4308M
[06/30 14:27:08 d2.utils.events]:  eta: 0:04:09  iter: 39419  total_loss: 0.08263  time: 0.4472  data_time: 0.0083  lr: 1e-06  max_mem: 4308M
[06/30 14:27:17 d2.utils.events]:  eta: 0:04:00  iter: 39439  total_loss: 0.0797  time: 0.4472  data_time: 0.0081  lr: 1e-06  max_mem: 4308M
[06/30 

[06/30 14:32:37 d2.evaluation.evaluator]: Inference done 787/3000. Dataloading: 0.0020 s/iter. Inference: 0.0471 s/iter. Eval: 0.0355 s/iter. Total: 0.0846 s/iter. ETA=0:03:07
[06/30 14:32:42 d2.evaluation.evaluator]: Inference done 847/3000. Dataloading: 0.0020 s/iter. Inference: 0.0471 s/iter. Eval: 0.0354 s/iter. Total: 0.0846 s/iter. ETA=0:03:02
[06/30 14:32:47 d2.evaluation.evaluator]: Inference done 908/3000. Dataloading: 0.0020 s/iter. Inference: 0.0471 s/iter. Eval: 0.0353 s/iter. Total: 0.0845 s/iter. ETA=0:02:56
[06/30 14:32:52 d2.evaluation.evaluator]: Inference done 968/3000. Dataloading: 0.0020 s/iter. Inference: 0.0471 s/iter. Eval: 0.0353 s/iter. Total: 0.0844 s/iter. ETA=0:02:51
[06/30 14:32:57 d2.evaluation.evaluator]: Inference done 1012/3000. Dataloading: 0.0020 s/iter. Inference: 0.0471 s/iter. Eval: 0.0365 s/iter. Total: 0.0857 s/iter. ETA=0:02:50
[06/30 14:33:02 d2.evaluation.evaluator]: Inference done 1037/3000. Dataloading: 0.0020 s/iter. Inference: 0.0474 s/ite

[06/30 14:36:25 d2.evaluation.evaluator]: Inference done 2158/3000. Dataloading: 0.0021 s/iter. Inference: 0.0519 s/iter. Eval: 0.0830 s/iter. Total: 0.1370 s/iter. ETA=0:01:55
[06/30 14:36:30 d2.evaluation.evaluator]: Inference done 2215/3000. Dataloading: 0.0021 s/iter. Inference: 0.0517 s/iter. Eval: 0.0819 s/iter. Total: 0.1358 s/iter. ETA=0:01:46
[06/30 14:36:36 d2.evaluation.evaluator]: Inference done 2273/3000. Dataloading: 0.0021 s/iter. Inference: 0.0516 s/iter. Eval: 0.0808 s/iter. Total: 0.1345 s/iter. ETA=0:01:37
[06/30 14:36:41 d2.evaluation.evaluator]: Inference done 2332/3000. Dataloading: 0.0021 s/iter. Inference: 0.0515 s/iter. Eval: 0.0796 s/iter. Total: 0.1333 s/iter. ETA=0:01:29
[06/30 14:36:46 d2.evaluation.evaluator]: Inference done 2388/3000. Dataloading: 0.0021 s/iter. Inference: 0.0513 s/iter. Eval: 0.0787 s/iter. Total: 0.1323 s/iter. ETA=0:01:20
[06/30 14:36:51 d2.evaluation.evaluator]: Inference done 2444/3000. Dataloading: 0.0021 s/iter. Inference: 0.0512 s

# Evaluate

## Models for Construction

### 1. Day

In [35]:
trainer_day = Detectron2Trainer('combined_all_train', 'combined_all_val', output_folder='./output_day_40k')
trainer_day.test()
#Vary the second argument -- validation -- to get performance on different cases (ex. weather, time of day)

17
[06/30 15:02:57 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/30 15:02:57 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/30 15:02:57 d2.data.build]: Using training sampler TrainingSampler
[06/30 15:02:57 d2.data.common]: Serializing 22288 elements to byte tensors and concatenating them all ...
[06/30 15:02:57 d2.data.common]: Serialized dataset takes 6.80 MiB
Last checkpoint: model_final.pth
[06/30 15:02:58 d2.checkpoint.c2_model_loading]: Following weights matched with model:
| Names in Model                       | Names in Checkpoint                                                                                  | Shapes                                          |
|:-------------------------------------|:-----------------------------------------------------------------------------------------------------|:------------------------------------------------|
| backbone.bottom_up.res2.0.conv1.*    | backbone.botto

[06/30 15:02:58 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in inference: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice')]
[06/30 15:02:58 d2.data.common]: Serializing 2000 elements to byte tensors and concatenating them all ...
[06/30 15:02:58 d2.data.common]: Serialized dataset takes 0.60 MiB
[06/30 15:02:58 d2.evaluation.evaluator]: Start inference on 2000 batches
[06/30 15:02:59 d2.evaluation.evaluator]: Inference done 11/2000. Dataloading: 0.0015 s/iter. Inference: 0.0479 s/iter. Eval: 0.0389 s/iter. Total: 0.0883 s/iter. ETA=0:02:55
[06/30 15:03:04 d2.evaluation.evaluator]: Inference done 69/2000. Dataloading: 0.0018 s/iter. Inference: 0.0457 s/iter. Eval: 0.0389 s/iter. Total: 0.0865 s/iter. ETA=0:02:46
[06/30 15:03:09 d2.evaluation.evaluator]: Inference done 128/2000. Dataloading: 0.0018 s/iter. Inference: 0.0456 s/iter. Eval: 0.0384 s/iter. Total: 0.0859 s/iter. ETA=0:02:40
[06/30 15:03:14 d2.evaluation.evaluator]: Infere

[06/30 15:06:32 d2.evaluation.evaluator]: Inference done 1668/2000. Dataloading: 0.0020 s/iter. Inference: 0.0504 s/iter. Eval: 0.0756 s/iter. Total: 0.1282 s/iter. ETA=0:00:42
[06/30 15:06:37 d2.evaluation.evaluator]: Inference done 1694/2000. Dataloading: 0.0020 s/iter. Inference: 0.0505 s/iter. Eval: 0.0766 s/iter. Total: 0.1292 s/iter. ETA=0:00:39
[06/30 15:06:42 d2.evaluation.evaluator]: Inference done 1720/2000. Dataloading: 0.0020 s/iter. Inference: 0.0506 s/iter. Eval: 0.0775 s/iter. Total: 0.1302 s/iter. ETA=0:00:36
[06/30 15:06:47 d2.evaluation.evaluator]: Inference done 1745/2000. Dataloading: 0.0020 s/iter. Inference: 0.0507 s/iter. Eval: 0.0784 s/iter. Total: 0.1312 s/iter. ETA=0:00:33
[06/30 15:06:52 d2.evaluation.evaluator]: Inference done 1771/2000. Dataloading: 0.0020 s/iter. Inference: 0.0508 s/iter. Eval: 0.0793 s/iter. Total: 0.1322 s/iter. ETA=0:00:30
[06/30 15:06:57 d2.evaluation.evaluator]: Inference done 1796/2000. Dataloading: 0.0020 s/iter. Inference: 0.0509 s

### 2. Night

In [37]:
trainer_night = Detectron2Trainer('carla_night_all_train', 'carla_night_all_val', output_folder='./output_night_40k')
trainer_night.test()

17
[06/30 15:48:01 d2.engine.defaults]: Model:
SemanticSegmentor(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
     

[06/30 15:48:01 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in training: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice'), RandomFlip()]
[06/30 15:48:01 d2.data.build]: Using training sampler TrainingSampler
[06/30 15:48:01 d2.data.common]: Serializing 15446 elements to byte tensors and concatenating them all ...
[06/30 15:48:01 d2.data.common]: Serialized dataset takes 5.05 MiB
Last checkpoint: model_final.pth
[06/30 15:48:02 d2.checkpoint.c2_model_loading]: Following weights matched with model:
| Names in Model                       | Names in Checkpoint                                                                                  | Shapes                                          |
|:-------------------------------------|:-----------------------------------------------------------------------------------------------------|:------------------------------------------------|
| backbone.bottom_up.res2.0.conv1.*    | backbone.botto

[06/30 15:48:02 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in inference: [ResizeShortestEdge(short_edge_length=(720, 720), max_size=2048, sample_style='choice')]
[06/30 15:48:02 d2.data.common]: Serializing 2000 elements to byte tensors and concatenating them all ...
[06/30 15:48:02 d2.data.common]: Serialized dataset takes 0.63 MiB
[06/30 15:48:02 d2.evaluation.evaluator]: Start inference on 2000 batches
[06/30 15:48:03 d2.evaluation.evaluator]: Inference done 11/2000. Dataloading: 0.0015 s/iter. Inference: 0.0496 s/iter. Eval: 0.0406 s/iter. Total: 0.0918 s/iter. ETA=0:03:02
[06/30 15:48:08 d2.evaluation.evaluator]: Inference done 69/2000. Dataloading: 0.0018 s/iter. Inference: 0.0461 s/iter. Eval: 0.0398 s/iter. Total: 0.0878 s/iter. ETA=0:02:49
[06/30 15:48:13 d2.evaluation.evaluator]: Inference done 127/2000. Dataloading: 0.0018 s/iter. Inference: 0.0459 s/iter. Eval: 0.0400 s/iter. Total: 0.0877 s/iter. ETA=0:02:44
[06/30 15:48:18 d2.evaluation.evaluator]: Infere

[06/30 15:50:55 d2.engine.defaults]: Evaluation results for carla_night_all_val in csv format:
[06/30 15:50:55 d2.evaluation.testing]: copypaste: Task: sem_seg
[06/30 15:50:55 d2.evaluation.testing]: copypaste: mIoU,fwIoU,mACC,pACC
[06/30 15:50:55 d2.evaluation.testing]: copypaste: 29.7557,64.1196,50.5246,77.5700


### 3. Day and Night

In [ ]:
trainer_both = Detectron2Trainer('combined_all_night_train', 'combined_all_night_val', output_folder='./output_both_40k')
trainer_both.test()

## 3. Model trained on all with carla night

In [ ]:
#trainer_all = Detectron2Trainer('combined_all_night_train', 'carla_rain_val', output_folder='./output_part_night_40k')
#trainer_all.test()

In [ ]:
#trainer_all = Detectron2Trainer('combined_all_night_train', 'carla_night_rain_val', output_folder='./output_part_night_40k')
#trainer_all.test()

In [ ]:
#trainer_all = Detectron2Trainer('combined_all_night_train', 'cityscapes_rain_val', output_folder='./output_part_night_40k')
#trainer_all.test()

In [ ]:
#trainer_all = Detectron2Trainer('combined_all_night_train', 'cityscapes_clear_val', output_folder='./output_part_night_40k')
#trainer_all.test()

## 2. Model trained on all

In [ ]:
# trainer_all = Detectron2Trainer('combined_all_train', 'combined_all_val', output_folder='./output_combined_all_40k')
# trainer_all.test()

In [ ]:
# trainer_all = Detectron2Trainer('combined_all_train', 'combined_clear_val', output_folder='./output_combined_all_40k')
# trainer_all.test()

In [ ]:
# trainer_all = Detectron2Trainer('combined_all_train', 'combined_rain_val', output_folder='./output_combined_all_40k')
# trainer_all.test()

In [ ]:
# trainer_all = Detectron2Trainer('combined_all_train', 'carla_rain_val', output_folder='./output_combined_all_40k')
# trainer_all.test()

In [ ]:
# trainer_all = Detectron2Trainer('combined_all_train', 'cityscapes_rain_val', output_folder='./output_combined_all_40k')
# trainer_all.test()

In [ ]:
# trainer_all = Detectron2Trainer('combined_all_train', 'carla_clear_val', output_folder='./output_combined_all_40k')
# trainer_all.test()

In [ ]:
# trainer_all = Detectron2Trainer('combined_all_train', 'carla_night_rain_val', output_folder='./output_combined_all_40k')
# trainer_all.test()

## 1. Model trained on clear

In [ ]:
#trainer_clear = Detectron2Trainer('combined_clear_train', 'combined_all_val', output_folder='./output_combined_clear_20k')
#trainer_clear.test()

In [ ]:
#trainer_clear = Detectron2Trainer('combined_clear_train', 'combined_clear_val', output_folder='./output_combined_clear_20k')
#trainer_clear.test()

In [ ]:
#trainer_clear = Detectron2Trainer('combined_clear_train', 'combined_rain_val', output_folder='./output_combined_clear_20k')
#trainer_clear.test()

In [ ]:
#trainer_clear = Detectron2Trainer('combined_clear_train', 'carla_rain_val', output_folder='./output_combined_clear_20k')
#trainer_clear.test()

In [ ]:
#trainer_clear = Detectron2Trainer('combined_clear_train', 'cityscapes_rain_val', output_folder='./output_combined_clear_20k')
#trainer_clear.test()

In [ ]:
#trainer_clear = Detectron2Trainer('combined_clear_train', 'carla_clear_val', output_folder='./output_combined_clear_20k')
#trainer_clear.test()

In [ ]:
#trainer_clear = Detectron2Trainer('combined_clear_train', 'carla_night_rain_val', output_folder='./output_combined_clear_20k')
#trainer_clear.test()